In [1]:
# 1. Install kagglehub (if not already installed)
!pip install kagglehub


import kagglehub

# Download latest version
path = kagglehub.dataset_download("mikolajbabula/disaster-images-dataset-cnn-model")

print("Path to dataset files:", path)


[notice] A new release of pip is available: 25.0.1 -> 25.2
[notice] To update, run: C:\Users\chand\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip
C:\Users\chand\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


 18%|█▊        | 513M/2.79G [00:47<03:35, 11.4MB/s]  


ChunkedEncodingError: ('Connection broken: IncompleteRead(538066213 bytes read, 2455043351 more expected)', IncompleteRead(538066213 bytes read, 2455043351 more expected))

In [ ]:
!pip install gTTS

In [ ]:
# save this as generate_hazard_audios.py
import os
import pandas as pd
from gtts import gTTS   # pip install gTTS

# Path to your CSV
CSV_PATH = "labels.csv"   # update if needed
OUTPUT_DIR = "hazard_audios"
os.makedirs(OUTPUT_DIR, exist_ok=True)

# Load the CSV
df = pd.read_csv(CSV_PATH)

for i, row in df.iterrows():
    text = str(row.get("text", ""))   # column name holding hazard description
    if not text:
        continue
    tts = gTTS(text, lang="en")       # change lang if needed
    out_file = os.path.join(OUTPUT_DIR, f"hazard_{i}.mp3")
    tts.save(out_file)
    if i >= 9999:                     # stop after 10,000
        break

print(f"Generated {min(len(df), 10000)} audio files in {OUTPUT_DIR}")


In [ ]:
"""
Multimodal Hazard Detection & Fusion Pipeline (Enhanced with dataset path options)
- Handles separate dataset files for text (required) and optional image, video, audio.
- Uses location (latitude/longitude) when available; extracts from text if present.
- Computes a wave-altitude proxy using monocular depth estimation for images.
- Produces combined prediction: hazard_type, urgency_label, prior_hazard_at_location (true/false), review_tag, duplicate_flag (true/false), probability (0-1).
- Clusters duplicate/similar posts and gives priority to posts with multiple user reports.

Usage examples:
    python pipeline.py --text_csv /path/to/text.csv
    # or with optional modalities:
    python pipeline.py --text_csv /path/to/text.csv --image_csv /path/to/images.csv --audio_csv /path/to/audio.csv --video_csv /path/to/video.csv

Dependencies: torch, transformers, torchvision, torchaudio, sentence-transformers, opencv-python, scikit-learn, pandas, numpy, pillow, matplotlib
"""

import os
import re
import json
import argparse
from typing import List, Dict, Any, Tuple

import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, accuracy_score
from sklearn.cluster import DBSCAN
from sklearn.preprocessing import StandardScaler

import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms, models
from PIL import Image

from sentence_transformers import SentenceTransformer
import torchaudio
import cv2

LATLON_REGEX = re.compile(r"([-+]?\d{1,3}\.\d+)[,\s]+([-+]?\d{1,3}\.\d+)")

# ---- Data Loading ----

def load_dataset(path: str) -> List[Dict]:
    """Load dataset from CSV or JSON file."""
    ext = os.path.splitext(path)[1].lower()
    records = []
    if ext == '.csv':
        df = pd.read_csv(path)
        records = df.to_dict(orient='records')
    elif ext == '.json':
        with open(path,'r') as f:
            records = json.load(f)
    else:
        raise ValueError("Unsupported file type. Use CSV or JSON.")
    for r in records:
        r.setdefault('video_frames', [])
    return records

class MultimodalDataset(Dataset):
    def __init__(self, records: List[Dict], transform=None, text_embedder=None):
        self.records = records
        self.transform = transform
        self.text_embedder = text_embedder

    def __len__(self):
        return len(self.records)

    def _load_image(self, path):
        try:
            img = Image.open(path).convert('RGB')
            if self.transform:
                img = self.transform(img)
            return img
        except Exception:
            return torch.zeros(3,224,224)

    def _embed_text(self, text):
        if not text or not self.text_embedder:
            return np.zeros(self.text_embedder.get_sentence_embedding_dimension() if self.text_embedder else 768)
        return self.text_embedder.encode(text)

    def _load_audio(self, path):
        try:
            waveform, sr = torchaudio.load(path)
            if waveform.shape[0] > 1:
                waveform = waveform.mean(dim=0, keepdim=True)
            if sr != 16000:
                resampler = torchaudio.transforms.Resample(sr, 16000)
                waveform = resampler(waveform)
            mel = torchaudio.transforms.MelSpectrogram(sample_rate=16000, n_mels=64)(waveform)
            log_mel = torch.log1p(mel)
            return log_mel.mean(dim=-1).squeeze().numpy()
        except Exception:
            return np.zeros(64)

    def __getitem__(self, idx):
        r = self.records[idx]
        item = {}
        item['text_embedding'] = self._embed_text(r.get('text',''))
        if r.get('image_path'):
            item['image'] = self._load_image(r['image_path'])
        else:
            item['image'] = torch.zeros(3,224,224)
        item['video_frame_paths'] = r.get('video_frames', [])
        if r.get('audio_path'):
            item['audio_embedding'] = self._load_audio(r['audio_path'])
        else:
            item['audio_embedding'] = np.zeros(64)
        item['lat'] = r.get('lat', None)
        item['lon'] = r.get('lon', None)
        item['label'] = r.get('label', None)
        item['user_id'] = r.get('user_id', None)
        item['raw_record'] = r
        return item

class ImageEmbeddingModel(nn.Module):
    def __init__(self, device='cpu'):
        super().__init__()
        self.device = device
        self.backbone = models.resnet18(pretrained=True)
        self.backbone.fc = nn.Identity()
        self.to(device)

    def forward(self, x):
        return self.backbone(x)

def extract_latlon_from_text(text: str) -> Tuple[float,float]:
    if not text:
        return None, None
    m = LATLON_REGEX.search(text)
    if m:
        try:
            lat = float(m.group(1))
            lon = float(m.group(2))
            return lat, lon
        except:
            return None, None
    return None, None

def compute_wave_altitude_from_image(image_path: str) -> float:
    try:
        import torch.hub
        midas = torch.hub.load('intel-isl/MiDaS', 'MiDaS_small')
        midas.eval()
        transform = torch.hub.load('intel-isl/MiDaS', 'transforms').small_transform
        img = Image.open(image_path).convert('RGB')
        input_batch = transform(img).unsqueeze(0)
        with torch.no_grad():
            prediction = midas(input_batch)
            depth = prediction.squeeze().cpu().numpy()
        return float(depth.std())
    except Exception:
        return 0.0

def train_text_model(text_embeddings: np.ndarray, labels: np.ndarray, num_classes: int):
    from sklearn.linear_model import LogisticRegression
    clf = LogisticRegression(max_iter=1000)
    clf.fit(text_embeddings, labels)
    return clf

def train_image_model(image_features: np.ndarray, labels: np.ndarray):
    from sklearn.ensemble import RandomForestClassifier
    clf = RandomForestClassifier(n_estimators=100)
    clf.fit(image_features, labels)
    return clf

def train_audio_model(audio_features: np.ndarray, labels: np.ndarray):
    from sklearn.ensemble import RandomForestClassifier
    clf = RandomForestClassifier(n_estimators=100)
    clf.fit(audio_features, labels)
    return clf

def combine_models_stack(stack_X: np.ndarray, labels: np.ndarray):
    from sklearn.linear_model import LogisticRegression
    meta = LogisticRegression(max_iter=1000)
    meta.fit(stack_X, labels)
    return meta

def cluster_duplicates(embeddings: np.ndarray, eps=0.5, min_samples=2):
    sc = StandardScaler()
    Xs = sc.fit_transform(embeddings)
    db = DBSCAN(eps=eps, min_samples=min_samples, metric='cosine')
    return db.fit_predict(Xs)

URGENCY_THRESHOLDS = {'danger': 0.8, 'review': 0.5}

def urgency_label_from_prob(p: float) -> str:
    if p >= URGENCY_THRESHOLDS['danger']:
        return 'danger/urgent action needed'
    elif p >= URGENCY_THRESHOLDS['review']:
        return 'urgent review needed'
    else:
        return 'low urgency'

def build_pipeline(text_csv: str,
                   image_csv: str = None,
                   audio_csv: str = None,
                   video_csv: str = None,
                   text_model=None,
                   image_model=None,
                   audio_model=None,
                   meta_model=None,
                   text_embedder_name='sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2',
                   device='cpu') -> List[Dict]:
    records = load_dataset(text_csv)
    text_embedder = SentenceTransformer(text_embedder_name)
    img_transform = transforms.Compose([
        transforms.Resize((224,224)),
        transforms.ToTensor(),
        transforms.Normalize([0.485,0.456,0.406],[0.229,0.224,0.225])
    ])
    img_backbone = ImageEmbeddingModel(device=device)
    img_backbone.eval()

    ds = MultimodalDataset(records, transform=img_transform, text_embedder=text_embedder)
    text_feats, image_feats, audio_feats, locs, user_ids = [], [], [], [], []

    for i in range(len(ds)):
        item = ds[i]
        text_feats.append(item['text_embedding'])
        with torch.no_grad():
            img_tensor = item['image'].unsqueeze(0).to(device)
            img_feat = img_backbone(img_tensor).cpu().numpy().squeeze()
        image_feats.append(img_feat)
        audio_feats.append(item['audio_embedding'])
        locs.append((item['lat'], item['lon']))
        user_ids.append(item['user_id'])

    text_feats = np.vstack(text_feats)
    image_feats = np.vstack(image_feats)
    audio_feats = np.vstack(audio_feats)

    labels = np.array([r.get('label') for r in records])
    label_present = not any([l is None for l in labels])
    if text_model is None and label_present:
        text_model = train_text_model(text_feats, labels, num_classes=len(np.unique(labels)))
    if image_model is None and label_present:
        image_model = train_image_model(image_feats, labels)
    if audio_model is None and label_present:
        audio_model = train_audio_model(audio_feats, labels)

    text_probs = text_model.predict_proba(text_feats)
    image_probs = image_model.predict_proba(image_feats)
    audio_probs = audio_model.predict_proba(audio_feats)

    combined_stack = np.vstack([text_probs.max(axis=1), image_probs.max(axis=1), audio_probs.max(axis=1)]).T
    if meta_model is None and label_present:
        meta_model = combine_models_stack(combined_stack, labels)

    final_probs = meta_model.predict_proba(combined_stack)[:,1]
    concat_emb = np.hstack([text_feats, image_feats[:, :128], audio_feats])
    cluster_ids = cluster_duplicates(concat_emb)

    prior_reported = []
    coords = np.array([[lat if lat is not None else np.nan, lon if lon is not None else np.nan] for lat,lon in locs])
    for i,(lat,lon) in enumerate(locs):
        flag = False
        if lat is not None and lon is not None:
            dists = np.sqrt(np.nansum((coords - np.array([lat,lon]))**2, axis=1))
            nearby = np.where((dists < 0.01) & (~np.isnan(dists)))[0]
            for j in nearby:
                if j != i and records[j].get('label')==1:
                    flag = True
                    break
        prior_reported.append(flag)

    outputs = []
    for i,r in enumerate(records):
        prob = float(final_probs[i])
        urgency = urgency_label_from_prob(prob)
        duplicate_flag = cluster_ids[i] != -1 and sum(cluster_ids==cluster_ids[i])>1
        same_cluster_idxs = np.where(cluster_ids==cluster_ids[i])[0] if cluster_ids[i]!=-1 else np.array([i])
        unique_users = set([user_ids[idx] for idx in same_cluster_idxs if user_ids[idx] is not None])
        high_priority = len(unique_users) > 1
        lat,lon = r.get('lat'), r.get('lon')
        if (lat is None or lon is None) and r.get('text'):
            ext_lat, ext_lon = extract_latlon_from_text(r.get('text'))
            if ext_lat is not None:
                lat,lon = ext_lat, ext_lon
        wave_alt = compute_wave_altitude_from_image(r['image_path']) if r.get('image_path') else None
        pred_label = (meta_model.predict(combined_stack[i:i+1])[0])
        hazard_type = r.get('hazard_type') or ("hazard" if pred_label==1 else "no_hazard")
        review_tag = 'review_needed' if prob >= URGENCY_THRESHOLDS['review'] and prob < URGENCY_THRESHOLDS['danger'] else ('confirm' if prob>=URGENCY_THRESHOLDS['danger'] else 'low_confidence')
        outputs.append({
            'record_id': r.get('id', i),
            'hazard_type': hazard_type,
            'urgency_label': urgency,
            'prior_hazard_at_location': prior_reported[i],
            'review_tag': review_tag,
            'duplicate_flag': bool(duplicate_flag),
            'probability': prob,
            'lat': lat,
            'lon': lon,
            'wave_altitude_proxy': wave_alt,
            'cluster_id': int(cluster_ids[i]) if cluster_ids[i] is not None else -1,
            'high_priority_due_to_multiple_users': bool(high_priority)
        })
    return outputs

if __name__ == '__main__':
    parser = argparse.ArgumentParser(description="Multimodal Hazard Detection Pipeline")
    parser.add_argument('--text_csv', required=True, help='/content/hazard_dataset.csv')
    parser.add_argument('--image_csv', help='/root/.cache/kagglehub/datasets/mikolajbabula/disaster-images-dataset-cnn-model/versions/1')
    parser.add_argument('--audio_csv', help='/content/hazard_audios')
    parser.add_argument('--video_csv', help='Path to video CSV dataset (optional)')
    args = parser.parse_args([
    "--text_csv", "/content/hazard_dataset.csv",
    "--image_csv", "/root/.cache/kagglehub/datasets/mikolajbabula/disaster-images-dataset-cnn-model/versions/1",
    "--audio_csv", "/content/hazard_audios",
    "--video_csv", "/content/path/to/video.csv"
])

    outputs = build_pipeline(args.text_csv, args.image_csv, args.audio_csv, args.video_csv, device='cpu')
    print(json.dumps(outputs, indent=2))


In [ ]:
import pandas as pd

# Your data
data = /usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning:
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
modules.json: 100%
 229/229 [00:00<00:00, 16.1kB/s]
config_sentence_transformers.json: 100%
 122/122 [00:00<00:00, 8.05kB/s]
README.md:
 3.89k/? [00:00<00:00, 395kB/s]
sentence_bert_config.json: 100%
 53.0/53.0 [00:00<00:00, 6.71kB/s]
config.json: 100%
 645/645 [00:00<00:00, 32.7kB/s]
model.safetensors: 100%
 471M/471M [00:10<00:00, 42.1MB/s]
tokenizer_config.json: 100%
 480/480 [00:00<00:00, 10.2kB/s]
tokenizer.json: 100%
 9.08M/9.08M [00:00<00:00, 17.2MB/s]
special_tokens_map.json: 100%
 239/239 [00:00<00:00, 3.42kB/s]
config.json: 100%
 190/190 [00:00<00:00, 3.15kB/s]
/usr/local/lib/python3.12/dist-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet18_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet18_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/resnet18-f37072fd.pth" to /root/.cache/torch/hub/checkpoints/resnet18-f37072fd.pth
100%|██████████| 44.7M/44.7M [00:00<00:00, 188MB/s]
[
  {
    "record_id": 0,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 10,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 11,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 12,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 13,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 14,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 15,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 16,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 17,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 18,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 19,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 20,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 21,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 22,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 23,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 24,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 25,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 26,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 27,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 28,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 29,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 30,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 31,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 32,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 33,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 34,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 35,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 36,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 37,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 38,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 39,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 40,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 41,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 42,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 43,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 44,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 45,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 46,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 47,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 48,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 49,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 50,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 51,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 52,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 53,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 54,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 55,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 56,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 57,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 58,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 59,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 60,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 61,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 62,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 63,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 64,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 65,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 66,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 67,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 68,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 69,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 70,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 71,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 72,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 73,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 74,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 75,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 76,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 77,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 78,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 79,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 80,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 81,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 82,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 83,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 84,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 85,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 86,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 87,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 88,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 89,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 90,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 91,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 92,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 93,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 94,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 95,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 96,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 97,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 98,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 99,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 100,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 101,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 102,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 103,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 104,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 105,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 106,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 107,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 108,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 109,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 110,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 111,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 112,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 113,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 114,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 115,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 116,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 117,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 118,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 119,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 120,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 121,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 122,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 123,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 124,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 125,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 126,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 127,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 128,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 129,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 130,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 131,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 132,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 133,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 134,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 135,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 136,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 137,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 138,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 139,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 140,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 141,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 142,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 143,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 144,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 145,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 146,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 147,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 148,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 149,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 150,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 151,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 152,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 153,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 154,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 155,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 156,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 157,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 158,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 159,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 160,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 161,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 162,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 163,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 164,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 165,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 166,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 167,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 168,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 169,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 170,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 171,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 172,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 173,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 174,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 175,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 176,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 177,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 178,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 179,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 180,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 181,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 182,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 183,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 184,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 185,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 186,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 187,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 188,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 189,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 190,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 191,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 192,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 193,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 194,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 195,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 196,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 197,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 198,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 199,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 200,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 201,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 202,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 203,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 204,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 205,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 206,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 207,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 208,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 209,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 210,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 211,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 212,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 213,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 214,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 215,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 216,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 217,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 218,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 219,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 220,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 221,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 222,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 223,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 224,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 225,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 226,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 227,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 228,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 229,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 230,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 231,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 232,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 233,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 234,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 235,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 236,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 237,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 238,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 239,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 240,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 241,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 242,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 243,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 244,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 245,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 246,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 247,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 248,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 249,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 250,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 251,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 252,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 253,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 254,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 255,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 256,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 257,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 258,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 259,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 260,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 261,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 262,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 263,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 264,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 265,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 266,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 267,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 268,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 269,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 270,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 271,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 272,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 273,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 274,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 275,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 276,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 277,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 278,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 279,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 280,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 281,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 282,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 283,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 284,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 285,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 286,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 287,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 288,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 289,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 290,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 291,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 292,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 293,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 294,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 295,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 296,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 297,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 298,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 299,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 300,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 301,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 302,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 303,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 304,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 305,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 306,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 307,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 308,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 309,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 310,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 311,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 312,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 313,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 314,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 315,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 316,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 317,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 318,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 319,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 320,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 321,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 322,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 323,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 324,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 325,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 326,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 327,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 328,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 329,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 330,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 331,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 332,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 333,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 334,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 335,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 336,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 337,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 338,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 339,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 340,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 341,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 342,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 343,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 344,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 345,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 346,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 347,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 348,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 349,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 350,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 351,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 352,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 353,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 354,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 355,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 356,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 357,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 358,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 359,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 360,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 361,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 362,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 363,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 364,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 365,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 366,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 367,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 368,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 369,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 370,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 371,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 372,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 373,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 374,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 375,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 376,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 377,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 378,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 379,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 380,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 381,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 382,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 383,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 384,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 385,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 386,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 387,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 388,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 389,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 390,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 391,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 392,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 393,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 394,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 395,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 396,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 397,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 398,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 399,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 400,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 401,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 402,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 403,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 404,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 405,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 406,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 407,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 408,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 409,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 410,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 411,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 412,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 413,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 414,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 415,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 416,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 417,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 418,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 419,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 420,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 421,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 422,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 423,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 424,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 425,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 426,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 427,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 428,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 429,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 430,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 431,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 432,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 433,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 434,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 435,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 436,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 437,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 438,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 439,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 440,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 441,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 442,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 443,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 444,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 445,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 446,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 447,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 448,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 449,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 450,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 451,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 452,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 453,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 454,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 455,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 456,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 457,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 458,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 459,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 460,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 461,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 462,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 463,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 464,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 465,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 466,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 467,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 468,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 469,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 470,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 471,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 472,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 473,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 474,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 475,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 476,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 477,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 478,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 479,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 480,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 481,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 482,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 483,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 484,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 485,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 486,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 487,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 488,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 489,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 490,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 491,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 492,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 493,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 494,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 495,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 496,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 497,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 498,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 499,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 500,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 501,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 502,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 503,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 504,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 505,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 506,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 507,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 508,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 509,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 510,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 511,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 512,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 513,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 514,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 515,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 516,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 517,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 518,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 519,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 520,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 521,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 522,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 523,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 524,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 525,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 526,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 527,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 528,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 529,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 530,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 531,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 532,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 533,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 534,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 535,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 536,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 537,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 538,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 539,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 540,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 541,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 542,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 543,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 544,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 545,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 546,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 547,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 548,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 549,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 550,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 551,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 552,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 553,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 554,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 555,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 556,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 557,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 558,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 559,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 560,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 561,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 562,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 563,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 564,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 565,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 566,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 567,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 568,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 569,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 570,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 571,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 572,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 573,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 574,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 575,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 576,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 577,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 578,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 579,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 580,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 581,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 582,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 583,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 584,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 585,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 586,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 587,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 588,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 589,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 590,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 591,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 592,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 593,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 594,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 595,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 596,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 597,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 598,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 599,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 600,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 601,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 602,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 603,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 604,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 605,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 606,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 607,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 608,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 609,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 610,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 611,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 612,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 613,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 614,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 615,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 616,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 617,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 618,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 619,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 620,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 621,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 622,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 623,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 624,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 625,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 626,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 627,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 628,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 629,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 630,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 631,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 632,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 633,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 634,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 635,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 636,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 637,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 638,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 639,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 640,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 641,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 642,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 643,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 644,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 645,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 646,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 647,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 648,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 649,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 650,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 651,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 652,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 653,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 654,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 655,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 656,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 657,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 658,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 659,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 660,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 661,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 662,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 663,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 664,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 665,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 666,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 667,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 668,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 669,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 670,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 671,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 672,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 673,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 674,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 675,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 676,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 677,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 678,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 679,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 680,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 681,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 682,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 683,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 684,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 685,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 686,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 687,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 688,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 689,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 690,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 691,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 692,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 693,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 694,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 695,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 696,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 697,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 698,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 699,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 700,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 701,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 702,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 703,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 704,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 705,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 706,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 707,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 708,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 709,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 710,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 711,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 712,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 713,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 714,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 715,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 716,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 717,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 718,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 719,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 720,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 721,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 722,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 723,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 724,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 725,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 726,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 727,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 728,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 729,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 730,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 731,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 732,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 733,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 734,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 735,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 736,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 737,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 738,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 739,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 740,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 741,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 742,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 743,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 744,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 745,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 746,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 747,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 748,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 749,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 750,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 751,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 752,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 753,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 754,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 755,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 756,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 757,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 758,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 759,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 760,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 761,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 762,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 763,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 764,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 765,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 766,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 767,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 768,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 769,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 770,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 771,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 772,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 773,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 774,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 775,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 776,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 777,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 778,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 779,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 780,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 781,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 782,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 783,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 784,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 785,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 786,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 787,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 788,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 789,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 790,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 791,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 792,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 793,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 794,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 795,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 796,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 797,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 798,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 799,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 800,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 801,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 802,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 803,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 804,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 805,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 806,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 807,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 808,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 809,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 810,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 811,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 812,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 813,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 814,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 815,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 816,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 817,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 818,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 819,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 820,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 821,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 822,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 823,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 824,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 825,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 826,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 827,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 828,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 829,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 830,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 831,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 832,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 833,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 834,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 835,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 836,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 837,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 838,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 839,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 840,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 841,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 842,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 843,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 844,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 845,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 846,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 847,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 848,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 849,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 850,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 851,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 852,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 853,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 854,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 855,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 856,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 857,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 858,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 859,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 860,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 861,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 862,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 863,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 864,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 865,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 866,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 867,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 868,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 869,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 870,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 871,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 872,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 873,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 874,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 875,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 876,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 877,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 878,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 879,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 880,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 881,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 882,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 883,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 884,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 885,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 886,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 887,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 888,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 889,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 890,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 891,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 892,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 893,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 894,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 895,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 896,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 897,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 898,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 899,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 900,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 901,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 902,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 903,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 904,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 905,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 906,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 907,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 908,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 909,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 910,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 911,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 912,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 913,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 914,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 915,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 916,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 917,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 918,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 919,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 920,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 921,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 922,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 923,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 924,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 925,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 926,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 927,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 928,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 929,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 930,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 931,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 932,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 933,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 934,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 935,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 936,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 937,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 938,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 939,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 940,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 941,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 942,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 943,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 944,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 945,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 946,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 947,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 948,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 949,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 950,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 951,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 952,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 953,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 954,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 955,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 956,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 957,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 958,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 959,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 960,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 961,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 962,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 963,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 964,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 965,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 966,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 967,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 968,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 969,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 970,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 971,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 972,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 973,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 974,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 975,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 976,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 977,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 978,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 979,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 980,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 981,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 982,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 983,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 984,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 985,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 986,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 987,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 988,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 989,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 990,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 991,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 992,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 993,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 994,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 995,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 996,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 997,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 998,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 999,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1000,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1001,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1002,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1003,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1004,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1005,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1006,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1007,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1008,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1009,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1010,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1011,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1012,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1013,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1014,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1015,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1016,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1017,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1018,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1019,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1020,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1021,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1022,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1023,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1024,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1025,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1026,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1027,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1028,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1029,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1030,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1031,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1032,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1033,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1034,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1035,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1036,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1037,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1038,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1039,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1040,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1041,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1042,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1043,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1044,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1045,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1046,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1047,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1048,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1049,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1050,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1051,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1052,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1053,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1054,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1055,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1056,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1057,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1058,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1059,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1060,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1061,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1062,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1063,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1064,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1065,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1066,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1067,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1068,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1069,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1070,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1071,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1072,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1073,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1074,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1075,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1076,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1077,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1078,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1079,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1080,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1081,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1082,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1083,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1084,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1085,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1086,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1087,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1088,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1089,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1090,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1091,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1092,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1093,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1094,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1095,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1096,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1097,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1098,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1099,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1100,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1101,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1102,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1103,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1104,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1105,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1106,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1107,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1108,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1109,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1110,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1111,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1112,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1113,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1114,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1115,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1116,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1117,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1118,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1119,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1120,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1121,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1122,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1123,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1124,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1125,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1126,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1127,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1128,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1129,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1130,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1131,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1132,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1133,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1134,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1135,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1136,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1137,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1138,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1139,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1140,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1141,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1142,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1143,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1144,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1145,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1146,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1147,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1148,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1149,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1150,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1151,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1152,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1153,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1154,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1155,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1156,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1157,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1158,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1159,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1160,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1161,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1162,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1163,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1164,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1165,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1166,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1167,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1168,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1169,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1170,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1171,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1172,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1173,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1174,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1175,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1176,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1177,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1178,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1179,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1180,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1181,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1182,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1183,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1184,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1185,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1186,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1187,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1188,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1189,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1190,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1191,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1192,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1193,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1194,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1195,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1196,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1197,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1198,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1199,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1200,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1201,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1202,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1203,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1204,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1205,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1206,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1207,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1208,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1209,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1210,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1211,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1212,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1213,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1214,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1215,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1216,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1217,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1218,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1219,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1220,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1221,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1222,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1223,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1224,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1225,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1226,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1227,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1228,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1229,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1230,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1231,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1232,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1233,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1234,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1235,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1236,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1237,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1238,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1239,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1240,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1241,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1242,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1243,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1244,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1245,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1246,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1247,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1248,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1249,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1250,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1251,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1252,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1253,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1254,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1255,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1256,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1257,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1258,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1259,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1260,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1261,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1262,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1263,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1264,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1265,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1266,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1267,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1268,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1269,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1270,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1271,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1272,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1273,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1274,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1275,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1276,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1277,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1278,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1279,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1280,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1281,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1282,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1283,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1284,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1285,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1286,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1287,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1288,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1289,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1290,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1291,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1292,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1293,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1294,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1295,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1296,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1297,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1298,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1299,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1300,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1301,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1302,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1303,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1304,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1305,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1306,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1307,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1308,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1309,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1310,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1311,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1312,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1313,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1314,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1315,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1316,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1317,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1318,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1319,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1320,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1321,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1322,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1323,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1324,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1325,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1326,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1327,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1328,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1329,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1330,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1331,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1332,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1333,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1334,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1335,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1336,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1337,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1338,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1339,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1340,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1341,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1342,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1343,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1344,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1345,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1346,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1347,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1348,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1349,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1350,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1351,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1352,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1353,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1354,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1355,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1356,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1357,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1358,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1359,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1360,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1361,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1362,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1363,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1364,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1365,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1366,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1367,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1368,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1369,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1370,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1371,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1372,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1373,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1374,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1375,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1376,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1377,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1378,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1379,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1380,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1381,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1382,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1383,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1384,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1385,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1386,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1387,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1388,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1389,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1390,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1391,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1392,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1393,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1394,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1395,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1396,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1397,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1398,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1399,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1400,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1401,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1402,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1403,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1404,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1405,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1406,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1407,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1408,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1409,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1410,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1411,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1412,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1413,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1414,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1415,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1416,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1417,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1418,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1419,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1420,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1421,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1422,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1423,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1424,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1425,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1426,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1427,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1428,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1429,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1430,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1431,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1432,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1433,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1434,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1435,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1436,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1437,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1438,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1439,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1440,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1441,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1442,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1443,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1444,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1445,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1446,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1447,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1448,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1449,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1450,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1451,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1452,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1453,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1454,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1455,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1456,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1457,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1458,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1459,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1460,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1461,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1462,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1463,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1464,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1465,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1466,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1467,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1468,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1469,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1470,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1471,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1472,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1473,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1474,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1475,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1476,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1477,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1478,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1479,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1480,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1481,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1482,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1483,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1484,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1485,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1486,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1487,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1488,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1489,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1490,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1491,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1492,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1493,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1494,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1495,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1496,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1497,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1498,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1499,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1500,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1501,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1502,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1503,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1504,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1505,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1506,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1507,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1508,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1509,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1510,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1511,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1512,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1513,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1514,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1515,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1516,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1517,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1518,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1519,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1520,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1521,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1522,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1523,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1524,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1525,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1526,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1527,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1528,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1529,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1530,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1531,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1532,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1533,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1534,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1535,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1536,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1537,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1538,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1539,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1540,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1541,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1542,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1543,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1544,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1545,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1546,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1547,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1548,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1549,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1550,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1551,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1552,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1553,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1554,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1555,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1556,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1557,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1558,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1559,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1560,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1561,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1562,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1563,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1564,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1565,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1566,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1567,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1568,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1569,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1570,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1571,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1572,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1573,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1574,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1575,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1576,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1577,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1578,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1579,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1580,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1581,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1582,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1583,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1584,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1585,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1586,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1587,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1588,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1589,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1590,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1591,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1592,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1593,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1594,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1595,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1596,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1597,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1598,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1599,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1600,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1601,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1602,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1603,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1604,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1605,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1606,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1607,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1608,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1609,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1610,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1611,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1612,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1613,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1614,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1615,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1616,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1617,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1618,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1619,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1620,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1621,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1622,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1623,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1624,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1625,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1626,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1627,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1628,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1629,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1630,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1631,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1632,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1633,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1634,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1635,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1636,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1637,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1638,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1639,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1640,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1641,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1642,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1643,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1644,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1645,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1646,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1647,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1648,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1649,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1650,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1651,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1652,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1653,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1654,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1655,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1656,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1657,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1658,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1659,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1660,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1661,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1662,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1663,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1664,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1665,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1666,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1667,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1668,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1669,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1670,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1671,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1672,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1673,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1674,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1675,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1676,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1677,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1678,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1679,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1680,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1681,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1682,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1683,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1684,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1685,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1686,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1687,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1688,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1689,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1690,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1691,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1692,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1693,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1694,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1695,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1696,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1697,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1698,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1699,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1700,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1701,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1702,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1703,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1704,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1705,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1706,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1707,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1708,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1709,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1710,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1711,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1712,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1713,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1714,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1715,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1716,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1717,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1718,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1719,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1720,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1721,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1722,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1723,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1724,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1725,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1726,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1727,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1728,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1729,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1730,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1731,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1732,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1733,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1734,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1735,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1736,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1737,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1738,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1739,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1740,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1741,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1742,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1743,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1744,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1745,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1746,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1747,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1748,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1749,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1750,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1751,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1752,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1753,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1754,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1755,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1756,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1757,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1758,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1759,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1760,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1761,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1762,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1763,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1764,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1765,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1766,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1767,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1768,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1769,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1770,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1771,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1772,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1773,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1774,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1775,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1776,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1777,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1778,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1779,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1780,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1781,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1782,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1783,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1784,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1785,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1786,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1787,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1788,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1789,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1790,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1791,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1792,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1793,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1794,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1795,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1796,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1797,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1798,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1799,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1800,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1801,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1802,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1803,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1804,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1805,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1806,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1807,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1808,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1809,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1810,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1811,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1812,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1813,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1814,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1815,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1816,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1817,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1818,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1819,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1820,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1821,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1822,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1823,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1824,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1825,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1826,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1827,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1828,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1829,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1830,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1831,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1832,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1833,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1834,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1835,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1836,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1837,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1838,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1839,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1840,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1841,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1842,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1843,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1844,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1845,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1846,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1847,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1848,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1849,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1850,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1851,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1852,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1853,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1854,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1855,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1856,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1857,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1858,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1859,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1860,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1861,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1862,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1863,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1864,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1865,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1866,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1867,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1868,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1869,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1870,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1871,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1872,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1873,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1874,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1875,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1876,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1877,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1878,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1879,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1880,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1881,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1882,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1883,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1884,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1885,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1886,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1887,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1888,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1889,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1890,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1891,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1892,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1893,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1894,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1895,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1896,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1897,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1898,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1899,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1900,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1901,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1902,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1903,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1904,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1905,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1906,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1907,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1908,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1909,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1910,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1911,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1912,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1913,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1914,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1915,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1916,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1917,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1918,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1919,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1920,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1921,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1922,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1923,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1924,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1925,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1926,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1927,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1928,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1929,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1930,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1931,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1932,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1933,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1934,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1935,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1936,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1937,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1938,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1939,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1940,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1941,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1942,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1943,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1944,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1945,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1946,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1947,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1948,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1949,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1950,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1951,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1952,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1953,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1954,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1955,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1956,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1957,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1958,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1959,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1960,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1961,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1962,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1963,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1964,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1965,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1966,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1967,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1968,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1969,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1970,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1971,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1972,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1973,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1974,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1975,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1976,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1977,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1978,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1979,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1980,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1981,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1982,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1983,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1984,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1985,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1986,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1987,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1988,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1989,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1990,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1991,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1992,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1993,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1994,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1995,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1996,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1997,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1998,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 1999,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2000,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2001,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2002,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2003,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2004,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2005,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2006,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2007,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2008,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2009,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2010,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2011,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2012,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2013,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2014,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2015,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2016,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2017,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2018,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2019,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2020,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2021,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2022,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2023,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2024,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2025,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2026,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2027,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2028,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2029,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2030,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2031,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2032,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2033,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2034,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2035,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2036,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2037,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2038,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2039,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2040,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2041,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2042,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2043,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2044,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2045,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2046,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2047,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2048,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2049,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2050,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2051,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2052,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2053,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2054,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2055,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2056,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2057,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2058,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2059,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2060,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2061,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2062,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2063,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2064,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2065,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2066,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2067,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2068,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2069,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2070,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2071,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2072,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2073,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2074,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2075,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2076,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2077,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2078,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2079,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2080,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2081,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2082,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2083,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2084,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2085,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2086,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2087,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2088,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2089,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2090,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2091,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2092,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2093,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2094,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2095,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2096,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2097,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2098,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2099,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2100,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2101,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2102,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2103,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2104,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2105,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2106,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2107,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2108,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2109,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2110,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2111,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2112,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2113,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2114,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2115,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2116,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2117,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2118,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2119,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2120,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2121,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2122,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2123,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2124,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2125,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2126,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2127,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2128,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2129,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2130,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2131,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2132,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2133,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2134,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2135,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2136,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2137,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2138,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2139,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2140,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2141,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2142,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2143,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2144,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2145,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2146,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2147,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2148,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2149,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2150,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2151,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2152,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2153,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2154,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2155,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2156,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2157,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2158,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2159,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2160,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2161,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2162,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2163,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2164,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2165,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2166,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2167,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2168,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2169,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2170,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2171,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2172,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2173,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2174,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2175,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2176,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2177,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2178,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2179,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2180,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2181,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2182,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2183,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2184,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2185,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2186,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2187,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2188,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2189,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2190,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2191,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2192,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2193,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2194,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2195,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2196,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2197,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2198,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2199,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2200,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2201,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2202,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2203,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2204,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2205,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2206,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2207,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2208,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2209,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2210,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2211,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2212,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2213,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2214,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2215,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2216,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2217,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2218,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2219,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2220,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2221,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2222,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2223,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2224,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2225,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2226,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2227,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2228,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2229,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2230,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2231,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2232,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2233,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2234,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2235,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2236,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2237,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2238,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2239,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2240,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2241,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2242,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2243,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2244,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2245,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2246,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2247,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2248,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2249,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2250,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2251,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2252,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2253,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2254,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2255,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2256,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2257,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2258,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2259,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2260,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2261,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2262,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2263,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2264,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2265,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2266,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2267,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2268,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2269,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2270,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2271,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2272,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2273,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2274,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2275,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2276,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2277,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2278,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2279,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2280,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2281,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2282,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2283,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2284,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2285,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2286,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2287,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2288,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2289,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2290,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2291,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2292,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2293,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2294,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2295,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2296,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2297,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2298,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2299,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2300,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2301,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2302,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2303,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2304,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2305,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2306,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2307,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2308,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2309,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2310,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2311,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2312,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2313,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2314,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2315,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2316,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2317,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2318,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2319,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2320,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2321,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2322,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2323,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2324,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2325,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2326,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2327,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2328,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2329,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2330,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2331,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2332,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2333,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2334,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2335,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2336,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2337,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2338,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2339,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2340,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2341,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2342,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2343,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2344,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2345,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2346,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2347,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2348,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2349,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2350,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2351,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2352,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2353,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2354,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2355,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2356,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2357,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2358,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2359,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2360,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2361,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2362,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2363,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2364,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2365,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2366,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2367,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2368,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2369,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2370,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2371,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2372,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2373,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2374,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2375,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2376,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2377,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2378,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2379,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2380,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2381,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2382,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2383,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2384,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2385,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2386,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2387,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2388,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2389,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2390,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2391,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2392,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2393,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2394,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2395,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2396,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2397,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2398,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2399,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2400,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2401,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2402,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2403,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2404,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2405,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2406,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2407,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2408,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2409,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2410,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2411,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2412,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2413,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2414,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2415,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2416,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2417,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2418,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2419,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2420,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2421,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2422,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2423,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2424,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2425,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2426,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2427,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2428,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2429,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2430,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2431,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2432,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2433,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2434,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2435,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2436,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2437,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2438,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2439,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2440,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2441,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2442,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2443,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2444,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2445,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2446,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2447,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2448,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2449,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2450,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2451,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2452,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2453,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2454,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2455,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2456,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2457,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2458,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2459,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2460,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2461,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2462,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2463,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2464,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2465,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2466,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2467,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2468,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2469,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2470,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2471,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2472,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2473,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2474,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2475,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2476,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2477,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2478,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2479,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2480,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2481,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2482,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2483,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2484,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2485,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2486,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2487,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2488,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2489,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2490,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2491,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2492,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2493,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2494,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2495,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2496,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2497,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2498,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2499,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2500,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2501,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2502,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2503,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2504,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2505,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2506,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2507,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2508,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2509,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2510,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2511,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2512,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2513,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2514,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2515,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2516,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2517,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2518,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2519,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2520,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2521,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2522,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2523,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2524,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2525,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2526,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2527,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2528,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2529,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2530,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2531,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2532,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2533,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2534,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2535,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2536,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2537,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2538,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2539,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2540,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2541,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2542,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2543,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2544,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2545,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2546,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2547,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2548,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2549,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2550,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2551,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2552,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2553,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2554,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2555,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2556,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2557,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2558,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2559,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2560,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2561,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2562,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2563,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2564,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2565,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2566,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2567,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2568,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2569,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2570,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2571,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2572,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2573,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2574,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2575,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2576,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2577,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2578,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2579,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2580,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2581,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2582,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2583,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2584,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2585,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2586,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2587,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2588,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2589,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2590,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2591,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2592,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2593,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2594,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2595,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2596,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2597,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2598,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2599,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2600,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2601,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2602,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2603,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2604,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2605,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2606,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2607,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2608,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2609,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2610,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2611,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2612,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2613,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2614,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2615,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2616,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2617,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2618,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2619,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2620,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2621,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2622,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2623,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2624,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2625,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2626,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2627,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2628,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2629,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2630,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2631,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2632,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2633,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2634,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2635,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2636,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2637,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2638,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2639,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2640,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2641,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2642,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2643,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2644,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2645,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2646,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2647,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2648,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2649,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2650,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2651,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2652,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2653,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2654,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2655,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2656,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2657,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2658,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2659,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2660,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2661,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2662,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2663,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2664,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2665,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2666,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2667,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2668,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2669,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2670,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2671,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2672,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2673,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2674,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2675,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2676,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2677,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2678,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2679,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2680,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2681,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2682,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2683,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2684,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2685,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2686,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2687,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2688,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2689,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2690,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2691,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2692,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2693,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2694,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2695,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2696,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2697,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2698,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2699,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2700,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2701,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2702,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2703,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2704,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2705,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2706,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2707,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2708,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2709,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2710,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2711,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2712,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2713,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2714,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2715,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2716,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2717,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2718,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2719,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2720,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2721,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2722,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2723,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2724,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2725,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2726,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2727,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2728,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2729,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2730,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2731,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2732,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2733,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2734,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2735,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2736,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2737,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2738,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2739,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2740,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2741,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2742,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2743,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2744,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2745,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2746,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2747,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2748,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2749,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2750,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2751,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2752,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2753,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2754,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2755,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2756,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2757,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2758,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2759,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2760,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2761,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2762,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2763,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2764,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2765,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2766,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2767,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2768,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2769,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2770,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2771,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2772,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2773,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2774,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2775,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2776,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2777,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2778,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2779,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2780,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2781,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2782,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2783,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2784,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2785,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2786,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2787,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2788,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2789,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2790,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2791,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2792,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2793,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2794,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2795,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2796,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2797,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2798,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2799,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2800,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2801,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2802,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2803,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2804,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2805,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2806,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2807,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2808,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2809,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2810,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2811,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2812,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2813,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2814,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2815,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2816,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2817,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2818,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2819,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2820,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2821,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2822,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2823,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2824,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2825,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2826,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2827,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2828,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2829,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2830,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2831,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2832,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2833,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2834,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2835,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2836,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2837,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2838,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2839,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2840,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2841,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2842,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2843,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2844,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2845,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2846,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2847,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2848,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2849,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2850,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2851,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2852,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2853,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2854,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2855,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2856,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2857,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2858,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2859,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2860,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2861,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2862,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2863,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2864,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2865,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2866,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2867,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2868,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2869,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2870,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2871,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2872,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2873,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2874,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2875,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2876,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2877,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2878,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2879,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2880,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2881,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2882,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2883,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2884,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2885,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2886,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2887,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2888,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2889,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2890,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2891,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2892,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2893,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2894,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2895,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2896,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2897,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2898,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2899,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2900,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2901,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2902,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2903,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2904,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2905,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2906,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2907,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2908,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2909,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2910,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2911,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2912,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2913,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2914,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2915,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2916,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2917,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2918,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2919,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2920,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2921,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2922,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2923,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2924,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2925,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2926,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2927,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2928,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2929,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2930,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2931,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2932,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2933,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2934,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2935,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2936,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2937,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2938,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2939,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2940,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2941,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2942,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2943,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2944,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2945,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2946,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2947,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2948,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2949,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2950,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2951,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2952,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2953,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2954,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2955,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2956,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2957,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2958,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2959,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2960,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2961,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2962,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2963,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2964,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2965,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2966,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2967,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2968,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2969,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2970,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2971,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2972,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2973,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2974,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2975,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2976,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2977,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2978,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2979,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2980,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2981,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2982,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2983,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2984,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2985,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2986,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2987,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2988,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2989,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2990,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2991,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2992,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2993,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2994,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2995,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2996,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2997,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2998,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 2999,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3000,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3001,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3002,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3003,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3004,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3005,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3006,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3007,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3008,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3009,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3010,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3011,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3012,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3013,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3014,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3015,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3016,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3017,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3018,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3019,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3020,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3021,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3022,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3023,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3024,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3025,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3026,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3027,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3028,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3029,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3030,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3031,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3032,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3033,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3034,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3035,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3036,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3037,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3038,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3039,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3040,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3041,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3042,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3043,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3044,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3045,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3046,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3047,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3048,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3049,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3050,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3051,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3052,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3053,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3054,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3055,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3056,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3057,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3058,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3059,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3060,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3061,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3062,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3063,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3064,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3065,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3066,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3067,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3068,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3069,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3070,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3071,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3072,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3073,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3074,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3075,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3076,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3077,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3078,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3079,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3080,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3081,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3082,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3083,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3084,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3085,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3086,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3087,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3088,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3089,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3090,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3091,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3092,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3093,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3094,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3095,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3096,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3097,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3098,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3099,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3100,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3101,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3102,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3103,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3104,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3105,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3106,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3107,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3108,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3109,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3110,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3111,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3112,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3113,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3114,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3115,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3116,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3117,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3118,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3119,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3120,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3121,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3122,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3123,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3124,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3125,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3126,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3127,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3128,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3129,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3130,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3131,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3132,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3133,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3134,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3135,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3136,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3137,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3138,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3139,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3140,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3141,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3142,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3143,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3144,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3145,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3146,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3147,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3148,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3149,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3150,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3151,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3152,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3153,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3154,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3155,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3156,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3157,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3158,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3159,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3160,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3161,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3162,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3163,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3164,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3165,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3166,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3167,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3168,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3169,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3170,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3171,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3172,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3173,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3174,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3175,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3176,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3177,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3178,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3179,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3180,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3181,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3182,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3183,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3184,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3185,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3186,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3187,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3188,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3189,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3190,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3191,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3192,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3193,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3194,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3195,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3196,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3197,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3198,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3199,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3200,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3201,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3202,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3203,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3204,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3205,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3206,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3207,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3208,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3209,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3210,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3211,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3212,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3213,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3214,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3215,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3216,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3217,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3218,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3219,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3220,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3221,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3222,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3223,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3224,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3225,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3226,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3227,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3228,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3229,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3230,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3231,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3232,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3233,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3234,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3235,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3236,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3237,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3238,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3239,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3240,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3241,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3242,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3243,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3244,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3245,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3246,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3247,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3248,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3249,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3250,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3251,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3252,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3253,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3254,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3255,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3256,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3257,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3258,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3259,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3260,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3261,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3262,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3263,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3264,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3265,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3266,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3267,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3268,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3269,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3270,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3271,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3272,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3273,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3274,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3275,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3276,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3277,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3278,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3279,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3280,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3281,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3282,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3283,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3284,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3285,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3286,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3287,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3288,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3289,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3290,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3291,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3292,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3293,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3294,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3295,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3296,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3297,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3298,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3299,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3300,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3301,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3302,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3303,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3304,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3305,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3306,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3307,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3308,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3309,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3310,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3311,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3312,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3313,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3314,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3315,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3316,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3317,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3318,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3319,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3320,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3321,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3322,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3323,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3324,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3325,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3326,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3327,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3328,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3329,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3330,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3331,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3332,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3333,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3334,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3335,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3336,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3337,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3338,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3339,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3340,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3341,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3342,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3343,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3344,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3345,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3346,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3347,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3348,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3349,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3350,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3351,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3352,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3353,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3354,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3355,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3356,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3357,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3358,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3359,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3360,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3361,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3362,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3363,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3364,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3365,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3366,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3367,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3368,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3369,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3370,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3371,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3372,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3373,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3374,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3375,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3376,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3377,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3378,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3379,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3380,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3381,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3382,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3383,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3384,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3385,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3386,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3387,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3388,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3389,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3390,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3391,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3392,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3393,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3394,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3395,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3396,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3397,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3398,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3399,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3400,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3401,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3402,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3403,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3404,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3405,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3406,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3407,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3408,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3409,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3410,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3411,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3412,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3413,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3414,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3415,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3416,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3417,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3418,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3419,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3420,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3421,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3422,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3423,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3424,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3425,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3426,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3427,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3428,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3429,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3430,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3431,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3432,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3433,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3434,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3435,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3436,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3437,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3438,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3439,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3440,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3441,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3442,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3443,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3444,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3445,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3446,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3447,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3448,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3449,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3450,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3451,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3452,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3453,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3454,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3455,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3456,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3457,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3458,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3459,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3460,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3461,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3462,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3463,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3464,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3465,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3466,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3467,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3468,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3469,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3470,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3471,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3472,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3473,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3474,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3475,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3476,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3477,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3478,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3479,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3480,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3481,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3482,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3483,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3484,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3485,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3486,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3487,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3488,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3489,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3490,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3491,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3492,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3493,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3494,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3495,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3496,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3497,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3498,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3499,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3500,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3501,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3502,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3503,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3504,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3505,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3506,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3507,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3508,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3509,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3510,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3511,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3512,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3513,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3514,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3515,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3516,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3517,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3518,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3519,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3520,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3521,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3522,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3523,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3524,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3525,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3526,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3527,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3528,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3529,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3530,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3531,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3532,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3533,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3534,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3535,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3536,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3537,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3538,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3539,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3540,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3541,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3542,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3543,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3544,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3545,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3546,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3547,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3548,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3549,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3550,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3551,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3552,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3553,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3554,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3555,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3556,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3557,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3558,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3559,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3560,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3561,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3562,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3563,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3564,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3565,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3566,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3567,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3568,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3569,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3570,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3571,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3572,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3573,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3574,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3575,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3576,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3577,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3578,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3579,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3580,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3581,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3582,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3583,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3584,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3585,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3586,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3587,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3588,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3589,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3590,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3591,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3592,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3593,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3594,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3595,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3596,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3597,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3598,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3599,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3600,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3601,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3602,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3603,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3604,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3605,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3606,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3607,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3608,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3609,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3610,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3611,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3612,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3613,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3614,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3615,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3616,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3617,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3618,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3619,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3620,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3621,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3622,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3623,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3624,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3625,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3626,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3627,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3628,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3629,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3630,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3631,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3632,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3633,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3634,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3635,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3636,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3637,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3638,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3639,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3640,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3641,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3642,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3643,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3644,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3645,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3646,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3647,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3648,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3649,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3650,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3651,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3652,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3653,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3654,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3655,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3656,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3657,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3658,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3659,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3660,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3661,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3662,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3663,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3664,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3665,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3666,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3667,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3668,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3669,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3670,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3671,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3672,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3673,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3674,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3675,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3676,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3677,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3678,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3679,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3680,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3681,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3682,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3683,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3684,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3685,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3686,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3687,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3688,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3689,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3690,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3691,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3692,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3693,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3694,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3695,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3696,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3697,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3698,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3699,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3700,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3701,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3702,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3703,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3704,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3705,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3706,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3707,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3708,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3709,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3710,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3711,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3712,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3713,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3714,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3715,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3716,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3717,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3718,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3719,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3720,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3721,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3722,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3723,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3724,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3725,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3726,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3727,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3728,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3729,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3730,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3731,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3732,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3733,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3734,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3735,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3736,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3737,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3738,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3739,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3740,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3741,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3742,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3743,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3744,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3745,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3746,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3747,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3748,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3749,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3750,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3751,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3752,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3753,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3754,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3755,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3756,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3757,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3758,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3759,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3760,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3761,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3762,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3763,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3764,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3765,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3766,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3767,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3768,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3769,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3770,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3771,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3772,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3773,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3774,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3775,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3776,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3777,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3778,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3779,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3780,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3781,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3782,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3783,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3784,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3785,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3786,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3787,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3788,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3789,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3790,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3791,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3792,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3793,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3794,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3795,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3796,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3797,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3798,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3799,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3800,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3801,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3802,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3803,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3804,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3805,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3806,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3807,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3808,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3809,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3810,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3811,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3812,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3813,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3814,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3815,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3816,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3817,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3818,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3819,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3820,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3821,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3822,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3823,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3824,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3825,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3826,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3827,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3828,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3829,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3830,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3831,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3832,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3833,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3834,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3835,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3836,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3837,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3838,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3839,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3840,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3841,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3842,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3843,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3844,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3845,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3846,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3847,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3848,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3849,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3850,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3851,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3852,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3853,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3854,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3855,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3856,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3857,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3858,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3859,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3860,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3861,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3862,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3863,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3864,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3865,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3866,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3867,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3868,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3869,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3870,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3871,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3872,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3873,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3874,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3875,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3876,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3877,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3878,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3879,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3880,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3881,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3882,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3883,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3884,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3885,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3886,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3887,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3888,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3889,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3890,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3891,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3892,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3893,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3894,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3895,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3896,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3897,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3898,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3899,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3900,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3901,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3902,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3903,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3904,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3905,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3906,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3907,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3908,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3909,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3910,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3911,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3912,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3913,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3914,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3915,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3916,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3917,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3918,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3919,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3920,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3921,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3922,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3923,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3924,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3925,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3926,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3927,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3928,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3929,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3930,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3931,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3932,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3933,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3934,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3935,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3936,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3937,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3938,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3939,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3940,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3941,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3942,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3943,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3944,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3945,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3946,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3947,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3948,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3949,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3950,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3951,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3952,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3953,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3954,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3955,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3956,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3957,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3958,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3959,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3960,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3961,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3962,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3963,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3964,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3965,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3966,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3967,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3968,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3969,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3970,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3971,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3972,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3973,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3974,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3975,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3976,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3977,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3978,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3979,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3980,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3981,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3982,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3983,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3984,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3985,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3986,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3987,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3988,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3989,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3990,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3991,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3992,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3993,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3994,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3995,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3996,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3997,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3998,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 3999,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4000,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4001,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4002,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4003,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4004,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4005,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4006,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4007,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4008,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4009,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4010,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4011,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4012,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4013,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4014,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4015,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4016,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4017,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4018,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4019,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4020,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4021,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4022,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4023,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4024,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4025,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4026,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4027,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4028,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4029,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4030,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4031,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4032,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4033,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4034,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4035,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4036,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4037,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4038,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4039,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4040,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4041,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4042,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4043,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4044,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4045,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4046,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4047,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4048,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4049,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4050,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4051,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4052,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4053,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4054,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4055,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4056,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4057,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4058,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4059,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4060,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4061,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4062,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4063,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4064,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4065,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4066,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4067,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4068,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4069,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4070,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4071,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4072,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4073,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4074,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4075,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4076,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4077,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4078,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4079,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4080,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4081,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4082,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4083,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4084,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4085,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4086,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4087,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4088,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4089,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4090,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4091,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4092,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4093,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4094,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4095,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4096,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4097,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4098,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4099,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4100,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4101,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4102,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4103,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4104,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4105,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4106,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4107,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4108,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4109,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4110,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4111,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4112,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4113,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4114,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4115,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4116,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4117,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4118,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4119,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4120,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4121,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4122,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4123,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4124,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4125,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4126,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4127,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4128,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4129,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4130,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4131,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4132,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4133,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4134,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4135,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4136,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4137,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4138,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4139,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4140,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4141,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4142,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4143,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4144,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4145,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4146,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4147,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4148,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4149,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4150,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4151,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4152,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4153,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4154,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4155,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4156,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4157,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4158,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4159,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4160,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4161,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4162,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4163,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4164,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4165,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4166,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4167,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4168,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4169,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4170,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4171,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4172,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4173,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4174,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4175,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4176,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4177,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4178,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4179,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4180,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4181,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4182,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4183,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4184,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4185,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4186,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4187,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4188,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4189,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4190,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4191,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4192,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4193,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4194,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4195,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4196,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4197,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4198,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4199,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4200,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4201,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4202,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4203,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4204,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4205,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4206,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4207,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4208,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4209,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4210,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4211,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4212,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4213,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4214,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4215,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4216,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4217,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4218,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4219,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4220,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4221,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4222,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4223,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4224,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4225,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4226,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4227,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4228,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4229,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4230,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4231,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4232,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4233,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4234,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4235,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4236,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4237,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4238,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4239,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4240,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4241,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4242,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4243,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4244,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4245,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4246,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4247,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4248,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4249,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4250,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4251,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4252,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4253,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4254,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4255,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4256,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4257,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4258,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4259,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4260,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4261,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4262,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4263,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4264,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4265,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4266,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4267,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4268,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4269,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4270,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4271,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4272,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4273,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4274,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4275,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4276,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4277,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4278,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4279,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4280,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4281,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4282,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4283,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4284,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4285,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4286,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4287,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4288,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4289,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4290,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4291,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4292,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4293,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4294,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4295,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4296,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4297,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4298,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4299,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4300,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4301,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4302,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4303,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4304,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4305,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4306,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4307,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4308,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4309,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4310,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4311,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4312,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4313,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4314,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4315,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4316,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4317,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4318,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4319,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4320,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4321,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4322,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4323,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4324,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4325,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4326,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4327,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4328,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4329,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4330,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4331,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4332,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4333,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4334,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4335,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4336,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4337,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4338,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4339,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4340,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4341,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4342,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4343,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4344,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4345,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4346,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4347,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4348,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4349,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4350,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4351,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4352,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4353,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4354,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4355,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4356,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4357,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4358,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4359,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4360,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4361,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4362,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4363,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4364,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4365,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4366,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4367,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4368,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4369,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4370,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4371,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4372,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4373,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4374,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4375,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4376,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4377,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4378,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4379,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4380,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4381,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4382,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4383,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4384,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4385,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4386,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4387,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4388,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4389,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4390,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4391,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4392,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4393,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4394,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4395,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4396,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4397,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4398,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4399,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4400,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4401,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4402,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4403,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4404,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4405,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4406,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4407,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4408,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4409,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4410,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4411,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4412,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4413,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4414,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4415,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4416,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4417,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4418,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4419,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4420,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4421,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4422,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4423,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4424,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4425,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4426,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4427,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4428,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4429,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4430,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4431,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4432,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4433,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4434,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4435,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4436,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4437,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4438,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4439,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4440,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4441,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4442,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4443,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4444,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4445,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4446,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4447,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4448,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4449,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4450,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4451,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4452,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4453,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4454,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4455,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4456,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4457,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4458,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4459,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4460,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4461,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4462,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4463,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4464,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4465,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4466,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4467,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4468,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4469,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4470,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4471,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4472,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4473,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4474,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4475,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4476,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4477,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4478,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4479,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4480,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4481,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4482,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4483,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4484,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4485,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4486,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4487,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4488,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4489,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4490,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4491,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4492,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4493,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4494,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4495,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4496,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4497,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4498,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4499,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4500,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4501,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4502,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4503,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4504,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4505,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4506,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4507,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4508,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4509,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4510,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4511,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4512,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4513,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4514,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4515,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4516,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4517,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4518,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4519,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4520,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4521,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4522,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4523,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4524,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4525,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4526,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4527,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4528,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4529,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4530,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4531,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4532,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4533,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4534,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4535,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4536,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4537,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4538,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4539,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4540,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4541,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4542,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4543,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4544,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4545,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4546,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4547,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4548,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4549,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4550,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4551,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4552,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4553,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4554,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4555,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4556,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4557,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4558,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4559,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4560,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4561,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4562,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4563,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4564,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4565,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4566,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4567,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4568,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4569,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4570,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4571,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4572,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4573,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4574,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4575,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4576,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4577,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4578,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4579,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4580,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4581,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4582,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4583,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4584,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4585,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4586,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4587,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4588,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4589,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4590,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4591,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4592,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4593,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4594,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4595,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4596,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4597,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4598,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4599,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4600,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4601,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4602,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4603,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4604,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4605,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4606,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4607,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4608,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4609,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4610,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4611,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4612,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4613,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4614,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4615,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4616,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4617,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4618,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4619,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4620,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4621,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4622,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4623,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4624,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4625,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4626,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4627,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4628,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4629,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4630,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4631,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4632,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4633,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4634,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4635,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4636,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4637,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4638,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4639,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4640,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4641,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4642,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4643,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4644,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4645,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4646,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4647,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4648,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4649,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4650,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4651,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4652,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4653,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4654,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4655,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4656,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4657,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4658,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4659,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4660,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4661,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4662,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4663,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4664,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4665,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4666,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4667,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4668,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4669,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4670,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4671,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4672,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4673,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4674,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4675,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4676,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4677,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4678,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4679,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4680,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4681,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4682,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4683,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4684,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4685,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4686,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4687,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4688,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4689,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4690,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4691,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4692,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4693,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4694,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4695,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4696,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4697,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4698,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4699,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4700,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4701,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4702,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4703,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4704,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4705,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4706,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4707,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4708,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4709,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4710,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4711,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4712,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4713,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4714,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4715,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4716,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4717,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4718,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4719,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4720,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4721,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4722,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4723,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4724,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4725,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4726,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4727,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4728,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4729,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4730,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4731,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4732,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4733,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4734,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4735,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4736,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4737,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4738,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4739,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4740,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4741,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4742,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4743,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4744,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4745,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4746,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4747,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4748,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4749,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4750,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4751,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4752,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4753,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4754,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4755,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4756,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4757,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4758,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4759,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4760,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4761,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4762,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4763,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4764,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4765,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4766,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4767,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4768,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4769,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4770,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4771,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4772,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4773,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4774,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4775,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4776,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4777,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4778,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4779,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4780,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4781,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4782,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4783,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4784,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4785,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4786,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4787,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4788,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4789,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4790,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4791,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4792,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4793,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4794,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4795,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4796,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4797,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4798,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4799,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4800,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4801,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4802,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4803,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4804,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4805,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4806,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4807,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4808,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4809,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4810,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4811,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4812,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4813,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4814,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4815,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4816,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4817,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4818,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4819,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4820,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4821,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4822,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4823,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4824,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4825,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4826,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4827,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4828,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4829,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4830,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4831,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4832,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4833,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4834,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4835,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4836,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4837,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4838,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4839,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4840,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4841,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4842,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4843,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4844,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4845,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4846,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4847,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4848,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4849,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4850,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4851,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4852,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4853,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4854,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4855,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4856,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4857,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4858,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4859,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4860,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4861,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4862,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4863,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4864,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4865,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4866,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4867,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4868,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4869,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4870,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4871,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4872,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4873,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4874,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4875,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4876,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4877,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4878,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4879,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4880,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4881,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4882,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4883,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4884,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4885,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4886,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4887,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4888,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4889,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4890,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4891,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4892,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4893,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4894,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4895,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4896,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4897,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4898,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4899,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4900,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4901,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4902,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4903,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4904,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4905,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4906,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4907,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4908,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4909,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4910,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4911,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4912,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4913,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4914,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4915,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4916,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4917,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4918,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4919,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4920,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4921,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4922,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4923,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4924,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4925,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4926,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4927,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4928,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4929,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4930,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4931,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4932,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4933,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4934,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4935,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4936,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4937,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4938,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4939,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4940,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4941,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4942,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4943,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4944,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4945,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4946,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4947,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4948,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4949,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4950,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4951,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4952,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4953,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4954,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4955,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4956,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4957,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4958,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4959,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4960,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4961,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4962,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4963,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4964,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4965,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4966,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4967,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4968,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4969,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4970,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4971,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4972,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4973,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4974,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4975,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4976,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4977,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4978,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4979,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4980,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4981,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4982,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4983,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4984,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4985,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4986,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4987,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4988,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4989,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4990,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4991,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4992,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4993,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4994,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4995,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4996,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4997,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4998,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 4999,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5000,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5001,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5002,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5003,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5004,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5005,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5006,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5007,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5008,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5009,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5010,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5011,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5012,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5013,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5014,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5015,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5016,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5017,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5018,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5019,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5020,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5021,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5022,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5023,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5024,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5025,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5026,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5027,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5028,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5029,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5030,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5031,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5032,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5033,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5034,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5035,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5036,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5037,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5038,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5039,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5040,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5041,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5042,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5043,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5044,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5045,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5046,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5047,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5048,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5049,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5050,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5051,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5052,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5053,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5054,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5055,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5056,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5057,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5058,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5059,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5060,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5061,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5062,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5063,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5064,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5065,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5066,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5067,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5068,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5069,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5070,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5071,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5072,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5073,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5074,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5075,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5076,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5077,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5078,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5079,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5080,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5081,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5082,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5083,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5084,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5085,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5086,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5087,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5088,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5089,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5090,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5091,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5092,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5093,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5094,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5095,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5096,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5097,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5098,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5099,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5100,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5101,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5102,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5103,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5104,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5105,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5106,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5107,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5108,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5109,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5110,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5111,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5112,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5113,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5114,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5115,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5116,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5117,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5118,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5119,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5120,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5121,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5122,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5123,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5124,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5125,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5126,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5127,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5128,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5129,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5130,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5131,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5132,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5133,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5134,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5135,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5136,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5137,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5138,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5139,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5140,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5141,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5142,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5143,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5144,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5145,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5146,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5147,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5148,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5149,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5150,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5151,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5152,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5153,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5154,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5155,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5156,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5157,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5158,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5159,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5160,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5161,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5162,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5163,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5164,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5165,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5166,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5167,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5168,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5169,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5170,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5171,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5172,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5173,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5174,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5175,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5176,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5177,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5178,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5179,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5180,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5181,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5182,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5183,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5184,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5185,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5186,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5187,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5188,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5189,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5190,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5191,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5192,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5193,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5194,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5195,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5196,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5197,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5198,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5199,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5200,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5201,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5202,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5203,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5204,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5205,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5206,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5207,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5208,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5209,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5210,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5211,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5212,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5213,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5214,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5215,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5216,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5217,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5218,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5219,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5220,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5221,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5222,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5223,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5224,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5225,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5226,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5227,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5228,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5229,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5230,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5231,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5232,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5233,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5234,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5235,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5236,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5237,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5238,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5239,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5240,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5241,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5242,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5243,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5244,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5245,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5246,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5247,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5248,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5249,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5250,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5251,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5252,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5253,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5254,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5255,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5256,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5257,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5258,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5259,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5260,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5261,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5262,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5263,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5264,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5265,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5266,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5267,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5268,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5269,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5270,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5271,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5272,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5273,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5274,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5275,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5276,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5277,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5278,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5279,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5280,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5281,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5282,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5283,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5284,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5285,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5286,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5287,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5288,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5289,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5290,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5291,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5292,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5293,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5294,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5295,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5296,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5297,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5298,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5299,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5300,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5301,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5302,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5303,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5304,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5305,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5306,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5307,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5308,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5309,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5310,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5311,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5312,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5313,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5314,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5315,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5316,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5317,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5318,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5319,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5320,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5321,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5322,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5323,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5324,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5325,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5326,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5327,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5328,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5329,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5330,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5331,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5332,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5333,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5334,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5335,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5336,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5337,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5338,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5339,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5340,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5341,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5342,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5343,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5344,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5345,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5346,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5347,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5348,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5349,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5350,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5351,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5352,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5353,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5354,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5355,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5356,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5357,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5358,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5359,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5360,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5361,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5362,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5363,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5364,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5365,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5366,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5367,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5368,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5369,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5370,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5371,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5372,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5373,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5374,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5375,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5376,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5377,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5378,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5379,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5380,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5381,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5382,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5383,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5384,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5385,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5386,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5387,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5388,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5389,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5390,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5391,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5392,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5393,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5394,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5395,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5396,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5397,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5398,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5399,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5400,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5401,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5402,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5403,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5404,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5405,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5406,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5407,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5408,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5409,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5410,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5411,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5412,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5413,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5414,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5415,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5416,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5417,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5418,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5419,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5420,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5421,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5422,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5423,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5424,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5425,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5426,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5427,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5428,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5429,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5430,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5431,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5432,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5433,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5434,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5435,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5436,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5437,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5438,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5439,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5440,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5441,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5442,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5443,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5444,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5445,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5446,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5447,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5448,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5449,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5450,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5451,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5452,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5453,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5454,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5455,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5456,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5457,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5458,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5459,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5460,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5461,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5462,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5463,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5464,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5465,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5466,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5467,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5468,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5469,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5470,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5471,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5472,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5473,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5474,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5475,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5476,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5477,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5478,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5479,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5480,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5481,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5482,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5483,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5484,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5485,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5486,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5487,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5488,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5489,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5490,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5491,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5492,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5493,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5494,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5495,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5496,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5497,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5498,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5499,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5500,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5501,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5502,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5503,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5504,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5505,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5506,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5507,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5508,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5509,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5510,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5511,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5512,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5513,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5514,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5515,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5516,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5517,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5518,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5519,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5520,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5521,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5522,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5523,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5524,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5525,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5526,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5527,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5528,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5529,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5530,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5531,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5532,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5533,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5534,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5535,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5536,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5537,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5538,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5539,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5540,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5541,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5542,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5543,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5544,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5545,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5546,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5547,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5548,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5549,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5550,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5551,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5552,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5553,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5554,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5555,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5556,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5557,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5558,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5559,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5560,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5561,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5562,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5563,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5564,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5565,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5566,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5567,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5568,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5569,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5570,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5571,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5572,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5573,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5574,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5575,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5576,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5577,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5578,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5579,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5580,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5581,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5582,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5583,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5584,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5585,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5586,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5587,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5588,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5589,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5590,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5591,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5592,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5593,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5594,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5595,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5596,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5597,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5598,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5599,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5600,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5601,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5602,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5603,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5604,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5605,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5606,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5607,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5608,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5609,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5610,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5611,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5612,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5613,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5614,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5615,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5616,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5617,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5618,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5619,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5620,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5621,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5622,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5623,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5624,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5625,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5626,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5627,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5628,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5629,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5630,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5631,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5632,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5633,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5634,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5635,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5636,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5637,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5638,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5639,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5640,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5641,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5642,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5643,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5644,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5645,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5646,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5647,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5648,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5649,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5650,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5651,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5652,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5653,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5654,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5655,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5656,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5657,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5658,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5659,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5660,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5661,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5662,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5663,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5664,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5665,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5666,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5667,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5668,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5669,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5670,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5671,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5672,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5673,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5674,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5675,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5676,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5677,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5678,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5679,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5680,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5681,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5682,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5683,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5684,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5685,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5686,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5687,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5688,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5689,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5690,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5691,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5692,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5693,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5694,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5695,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5696,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5697,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5698,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5699,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5700,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5701,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5702,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5703,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5704,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5705,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5706,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5707,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5708,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5709,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5710,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5711,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5712,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5713,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5714,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5715,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5716,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5717,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5718,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5719,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5720,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5721,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5722,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5723,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5724,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5725,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5726,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5727,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5728,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5729,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5730,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5731,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5732,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5733,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5734,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5735,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5736,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5737,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5738,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5739,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5740,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5741,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5742,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5743,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5744,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5745,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5746,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5747,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5748,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5749,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5750,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5751,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5752,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5753,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5754,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5755,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5756,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5757,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5758,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5759,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5760,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5761,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5762,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5763,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5764,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5765,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5766,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5767,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5768,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5769,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5770,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5771,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5772,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5773,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5774,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5775,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5776,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5777,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5778,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5779,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5780,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5781,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5782,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5783,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5784,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5785,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5786,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5787,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5788,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5789,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5790,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5791,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5792,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5793,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5794,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5795,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5796,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5797,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5798,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5799,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5800,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5801,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5802,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5803,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5804,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5805,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5806,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5807,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5808,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5809,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5810,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5811,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5812,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5813,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5814,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5815,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5816,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5817,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5818,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5819,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5820,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5821,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5822,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5823,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5824,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5825,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5826,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5827,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5828,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5829,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5830,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5831,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5832,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5833,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5834,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5835,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5836,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5837,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5838,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5839,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5840,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5841,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5842,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5843,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5844,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5845,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5846,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5847,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5848,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5849,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5850,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5851,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5852,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5853,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5854,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5855,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5856,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5857,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5858,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5859,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5860,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5861,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5862,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5863,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5864,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5865,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5866,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5867,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5868,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5869,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5870,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5871,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5872,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5873,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5874,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5875,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5876,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5877,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5878,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5879,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5880,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5881,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5882,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5883,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5884,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5885,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5886,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5887,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5888,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5889,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5890,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5891,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5892,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5893,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5894,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5895,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5896,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5897,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5898,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5899,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5900,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5901,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5902,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5903,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5904,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5905,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5906,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5907,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5908,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5909,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5910,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5911,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5912,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5913,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5914,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5915,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5916,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5917,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5918,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5919,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5920,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5921,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5922,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5923,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5924,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5925,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5926,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5927,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5928,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5929,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5930,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5931,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5932,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5933,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5934,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5935,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5936,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5937,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5938,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5939,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5940,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5941,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5942,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5943,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5944,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5945,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5946,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5947,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5948,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5949,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5950,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5951,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5952,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5953,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5954,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5955,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5956,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5957,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5958,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5959,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5960,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5961,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5962,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5963,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5964,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5965,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5966,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5967,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5968,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5969,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5970,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5971,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5972,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5973,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5974,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5975,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5976,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5977,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5978,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5979,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5980,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5981,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5982,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5983,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5984,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5985,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5986,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5987,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5988,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5989,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5990,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5991,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5992,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5993,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5994,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5995,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5996,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5997,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5998,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 5999,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6000,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6001,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6002,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6003,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6004,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6005,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6006,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6007,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6008,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6009,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6010,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6011,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6012,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6013,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6014,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6015,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6016,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6017,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6018,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6019,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6020,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6021,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6022,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6023,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6024,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6025,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6026,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6027,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6028,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6029,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6030,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6031,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6032,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6033,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6034,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6035,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6036,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6037,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6038,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6039,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6040,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6041,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6042,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6043,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6044,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6045,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6046,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6047,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6048,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6049,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6050,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6051,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6052,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6053,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6054,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6055,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6056,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6057,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6058,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6059,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6060,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6061,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6062,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6063,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6064,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6065,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6066,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6067,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6068,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6069,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6070,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6071,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6072,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6073,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6074,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6075,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6076,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6077,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6078,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6079,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6080,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6081,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6082,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6083,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6084,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6085,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6086,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6087,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6088,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6089,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6090,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6091,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6092,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6093,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6094,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6095,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6096,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6097,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6098,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6099,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6100,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6101,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6102,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6103,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6104,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6105,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6106,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6107,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6108,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6109,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6110,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6111,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6112,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6113,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6114,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6115,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6116,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6117,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6118,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6119,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6120,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6121,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6122,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6123,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6124,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6125,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6126,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6127,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6128,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6129,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6130,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6131,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6132,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6133,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6134,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6135,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6136,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6137,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6138,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6139,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6140,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6141,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6142,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6143,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6144,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6145,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6146,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6147,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6148,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6149,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6150,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6151,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6152,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6153,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6154,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6155,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6156,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6157,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6158,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6159,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6160,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6161,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6162,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6163,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6164,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6165,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6166,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6167,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6168,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6169,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6170,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6171,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6172,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6173,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6174,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6175,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6176,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6177,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6178,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6179,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6180,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6181,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6182,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6183,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6184,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6185,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6186,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6187,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6188,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6189,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6190,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6191,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6192,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6193,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6194,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6195,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6196,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6197,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6198,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6199,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6200,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6201,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6202,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6203,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6204,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6205,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6206,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6207,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6208,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6209,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6210,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6211,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6212,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6213,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6214,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6215,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6216,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6217,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6218,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6219,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6220,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6221,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6222,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6223,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6224,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6225,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6226,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6227,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6228,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6229,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6230,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6231,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6232,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6233,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6234,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6235,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6236,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6237,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6238,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6239,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6240,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6241,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6242,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6243,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6244,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6245,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6246,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6247,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6248,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6249,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6250,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6251,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6252,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6253,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6254,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6255,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6256,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6257,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6258,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6259,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6260,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6261,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6262,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6263,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6264,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6265,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6266,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6267,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6268,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6269,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6270,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6271,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6272,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6273,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6274,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6275,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6276,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6277,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6278,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6279,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6280,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6281,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6282,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6283,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6284,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6285,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6286,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6287,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6288,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6289,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6290,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6291,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6292,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6293,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6294,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6295,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6296,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6297,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6298,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6299,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6300,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6301,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6302,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6303,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6304,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6305,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6306,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6307,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6308,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6309,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6310,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6311,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6312,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6313,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6314,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6315,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6316,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6317,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6318,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6319,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6320,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6321,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6322,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6323,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6324,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6325,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6326,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6327,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6328,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6329,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6330,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6331,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6332,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6333,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6334,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6335,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6336,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6337,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6338,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6339,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6340,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6341,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6342,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6343,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6344,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6345,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6346,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6347,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6348,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6349,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6350,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6351,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6352,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6353,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6354,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6355,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6356,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6357,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6358,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6359,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6360,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6361,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6362,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6363,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6364,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6365,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6366,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6367,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6368,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6369,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6370,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6371,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6372,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6373,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6374,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6375,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6376,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6377,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6378,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6379,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6380,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6381,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6382,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6383,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6384,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6385,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6386,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6387,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6388,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6389,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6390,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6391,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6392,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6393,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6394,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6395,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6396,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6397,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6398,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6399,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6400,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6401,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6402,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6403,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6404,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6405,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6406,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6407,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6408,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6409,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6410,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6411,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6412,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6413,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6414,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6415,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6416,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6417,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6418,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6419,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6420,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6421,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6422,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6423,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6424,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6425,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6426,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6427,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6428,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6429,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6430,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6431,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6432,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6433,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6434,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6435,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6436,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6437,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6438,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6439,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6440,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6441,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6442,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6443,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6444,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6445,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6446,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6447,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6448,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6449,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6450,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6451,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6452,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6453,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6454,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6455,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6456,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6457,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6458,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6459,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6460,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6461,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6462,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6463,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6464,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6465,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6466,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6467,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6468,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6469,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6470,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6471,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6472,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6473,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6474,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6475,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6476,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6477,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6478,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6479,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6480,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6481,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6482,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6483,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6484,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6485,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6486,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6487,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6488,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6489,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6490,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6491,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6492,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6493,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6494,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6495,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6496,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6497,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6498,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6499,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6500,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6501,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6502,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6503,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6504,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6505,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6506,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6507,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6508,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6509,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6510,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6511,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6512,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6513,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6514,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6515,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6516,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6517,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6518,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6519,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6520,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6521,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6522,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6523,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6524,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6525,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6526,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6527,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6528,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6529,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6530,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6531,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6532,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6533,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6534,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6535,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6536,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6537,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6538,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6539,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6540,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6541,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6542,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6543,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6544,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6545,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6546,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6547,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6548,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6549,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6550,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6551,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6552,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6553,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6554,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6555,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6556,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6557,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6558,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6559,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6560,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6561,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6562,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6563,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6564,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6565,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6566,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6567,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6568,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6569,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6570,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6571,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6572,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6573,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6574,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6575,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6576,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6577,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6578,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6579,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6580,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6581,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6582,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6583,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6584,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6585,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6586,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6587,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6588,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6589,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6590,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6591,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6592,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6593,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6594,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6595,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6596,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6597,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6598,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6599,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6600,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6601,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6602,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6603,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6604,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6605,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6606,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6607,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6608,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6609,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6610,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6611,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6612,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6613,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6614,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6615,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6616,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6617,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6618,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6619,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6620,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6621,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6622,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6623,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6624,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6625,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6626,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6627,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6628,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6629,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6630,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6631,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6632,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6633,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6634,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6635,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6636,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6637,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6638,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6639,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6640,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6641,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6642,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6643,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6644,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6645,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6646,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6647,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6648,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6649,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6650,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6651,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6652,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6653,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6654,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6655,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6656,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6657,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6658,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6659,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6660,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6661,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6662,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6663,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6664,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6665,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6666,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6667,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6668,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6669,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6670,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6671,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6672,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6673,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6674,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6675,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6676,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6677,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6678,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6679,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6680,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6681,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6682,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6683,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6684,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6685,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6686,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6687,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6688,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6689,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6690,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6691,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6692,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6693,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6694,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6695,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6696,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6697,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6698,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6699,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6700,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6701,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6702,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6703,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6704,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6705,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6706,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6707,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6708,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6709,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6710,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6711,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6712,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6713,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6714,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6715,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6716,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6717,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6718,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6719,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6720,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6721,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6722,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6723,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6724,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6725,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6726,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6727,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6728,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6729,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6730,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6731,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6732,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6733,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6734,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6735,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6736,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6737,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6738,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6739,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6740,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6741,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6742,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6743,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6744,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6745,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6746,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6747,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6748,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6749,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6750,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6751,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6752,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6753,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6754,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6755,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6756,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6757,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6758,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6759,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6760,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6761,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6762,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6763,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6764,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6765,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6766,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6767,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6768,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6769,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6770,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6771,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6772,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6773,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6774,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6775,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6776,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6777,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6778,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6779,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6780,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6781,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6782,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6783,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6784,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6785,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6786,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6787,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6788,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6789,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6790,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6791,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6792,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6793,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6794,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6795,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6796,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6797,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6798,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6799,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6800,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6801,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6802,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6803,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6804,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6805,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6806,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6807,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6808,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6809,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6810,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6811,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6812,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6813,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6814,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6815,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6816,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6817,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6818,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6819,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6820,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6821,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6822,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6823,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6824,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6825,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6826,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6827,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6828,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6829,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6830,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6831,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6832,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6833,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6834,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6835,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6836,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6837,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6838,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6839,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6840,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6841,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6842,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6843,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6844,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6845,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6846,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6847,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6848,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6849,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6850,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6851,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6852,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6853,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6854,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6855,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6856,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6857,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6858,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6859,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6860,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6861,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6862,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6863,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6864,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6865,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6866,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6867,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6868,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6869,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6870,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6871,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6872,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6873,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6874,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6875,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6876,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6877,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6878,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6879,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6880,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6881,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6882,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6883,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6884,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6885,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6886,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6887,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6888,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6889,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6890,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6891,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6892,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6893,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6894,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6895,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6896,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6897,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6898,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6899,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6900,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6901,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6902,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6903,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6904,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6905,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6906,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6907,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6908,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6909,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6910,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6911,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6912,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6913,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6914,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6915,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6916,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6917,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6918,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6919,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6920,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6921,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6922,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6923,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6924,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6925,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6926,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6927,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6928,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6929,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6930,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6931,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6932,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6933,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6934,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6935,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6936,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6937,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6938,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6939,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6940,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6941,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6942,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6943,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6944,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6945,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6946,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6947,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6948,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6949,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6950,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6951,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6952,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6953,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6954,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6955,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6956,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6957,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6958,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6959,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6960,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6961,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6962,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6963,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6964,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6965,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6966,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6967,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6968,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6969,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6970,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6971,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6972,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6973,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6974,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6975,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6976,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6977,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6978,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6979,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6980,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6981,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6982,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6983,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6984,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6985,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6986,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6987,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6988,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6989,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6990,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6991,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6992,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6993,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6994,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6995,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6996,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6997,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6998,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 6999,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7000,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7001,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7002,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7003,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7004,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7005,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7006,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7007,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7008,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7009,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7010,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7011,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7012,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7013,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7014,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7015,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7016,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7017,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7018,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7019,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7020,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7021,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7022,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7023,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7024,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7025,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7026,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7027,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7028,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7029,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7030,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7031,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7032,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7033,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7034,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7035,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7036,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7037,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7038,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7039,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7040,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7041,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7042,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7043,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7044,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7045,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7046,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7047,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7048,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7049,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7050,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7051,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7052,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7053,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7054,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7055,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7056,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7057,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7058,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7059,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7060,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7061,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7062,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7063,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7064,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7065,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7066,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7067,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7068,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7069,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7070,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7071,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7072,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7073,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7074,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7075,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7076,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7077,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7078,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7079,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7080,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7081,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7082,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7083,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7084,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7085,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7086,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7087,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7088,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7089,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7090,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7091,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7092,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7093,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7094,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7095,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7096,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7097,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7098,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7099,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7100,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7101,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7102,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7103,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7104,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7105,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7106,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7107,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7108,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7109,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7110,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7111,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7112,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7113,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7114,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7115,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7116,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7117,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7118,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7119,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7120,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7121,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7122,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7123,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7124,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7125,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7126,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7127,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7128,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7129,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7130,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7131,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7132,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7133,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7134,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7135,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7136,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7137,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7138,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7139,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7140,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7141,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7142,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7143,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7144,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7145,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7146,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7147,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7148,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7149,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7150,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7151,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7152,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7153,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7154,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7155,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7156,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7157,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7158,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7159,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7160,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7161,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7162,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7163,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7164,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7165,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7166,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7167,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7168,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7169,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7170,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7171,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7172,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7173,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7174,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7175,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7176,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7177,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7178,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7179,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7180,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7181,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7182,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7183,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7184,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7185,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7186,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7187,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7188,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7189,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7190,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7191,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7192,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7193,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7194,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7195,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7196,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7197,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7198,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7199,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7200,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7201,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7202,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7203,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7204,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7205,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7206,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7207,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7208,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7209,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7210,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7211,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7212,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7213,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7214,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7215,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7216,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7217,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7218,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7219,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7220,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7221,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7222,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7223,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7224,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7225,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7226,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7227,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7228,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7229,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7230,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7231,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7232,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7233,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7234,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7235,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7236,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7237,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7238,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7239,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7240,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7241,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7242,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7243,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7244,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7245,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7246,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7247,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7248,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7249,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7250,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7251,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7252,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7253,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7254,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7255,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7256,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7257,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7258,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7259,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7260,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7261,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7262,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7263,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7264,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7265,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7266,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7267,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7268,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7269,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7270,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7271,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7272,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7273,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7274,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7275,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7276,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7277,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7278,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7279,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7280,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7281,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7282,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7283,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7284,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7285,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7286,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7287,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7288,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7289,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7290,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7291,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7292,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7293,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7294,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7295,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7296,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7297,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7298,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7299,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7300,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7301,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7302,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7303,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7304,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7305,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7306,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7307,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7308,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7309,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7310,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7311,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7312,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7313,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7314,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7315,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7316,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7317,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7318,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7319,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7320,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7321,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7322,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7323,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7324,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7325,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7326,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7327,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7328,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7329,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7330,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7331,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7332,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7333,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7334,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7335,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7336,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7337,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7338,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7339,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7340,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7341,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7342,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7343,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7344,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7345,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7346,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7347,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7348,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7349,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7350,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7351,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7352,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7353,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7354,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7355,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7356,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7357,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7358,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7359,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7360,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7361,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7362,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7363,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7364,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7365,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7366,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7367,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7368,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7369,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7370,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7371,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7372,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7373,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7374,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7375,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7376,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7377,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7378,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7379,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7380,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7381,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7382,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7383,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7384,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7385,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7386,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7387,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7388,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7389,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7390,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7391,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7392,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7393,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7394,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7395,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7396,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7397,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7398,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7399,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7400,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7401,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7402,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7403,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7404,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7405,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7406,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7407,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7408,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7409,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7410,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7411,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7412,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7413,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7414,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7415,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7416,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7417,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7418,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7419,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7420,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7421,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7422,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7423,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7424,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7425,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7426,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7427,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7428,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7429,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7430,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7431,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7432,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7433,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7434,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7435,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7436,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7437,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7438,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7439,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7440,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7441,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7442,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7443,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7444,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7445,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7446,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7447,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7448,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7449,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7450,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7451,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7452,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7453,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7454,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7455,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7456,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7457,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7458,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7459,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7460,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7461,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7462,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7463,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7464,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7465,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7466,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7467,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7468,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7469,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7470,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7471,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7472,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7473,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7474,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7475,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7476,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7477,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7478,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7479,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7480,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7481,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7482,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7483,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7484,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7485,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7486,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7487,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7488,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7489,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7490,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7491,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7492,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7493,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7494,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7495,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7496,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7497,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7498,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7499,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7500,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7501,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7502,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7503,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7504,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7505,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7506,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7507,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7508,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7509,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7510,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7511,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7512,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7513,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7514,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7515,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7516,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7517,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7518,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7519,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7520,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7521,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7522,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7523,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7524,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7525,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7526,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7527,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7528,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7529,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7530,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7531,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7532,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7533,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7534,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7535,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7536,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7537,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7538,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7539,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7540,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7541,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7542,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7543,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7544,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7545,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7546,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7547,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7548,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7549,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7550,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7551,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7552,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7553,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7554,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7555,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7556,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7557,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7558,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7559,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7560,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7561,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7562,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7563,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7564,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7565,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7566,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7567,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7568,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7569,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7570,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7571,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7572,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7573,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7574,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7575,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7576,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7577,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7578,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7579,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7580,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7581,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7582,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7583,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7584,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7585,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7586,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7587,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7588,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7589,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7590,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7591,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7592,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7593,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7594,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7595,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7596,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7597,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7598,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7599,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7600,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7601,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7602,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7603,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7604,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7605,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7606,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7607,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7608,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7609,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7610,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7611,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7612,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7613,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7614,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7615,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7616,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7617,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7618,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7619,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7620,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7621,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7622,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7623,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7624,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7625,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7626,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7627,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7628,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7629,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7630,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7631,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7632,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7633,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7634,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7635,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7636,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7637,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7638,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7639,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7640,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7641,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7642,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7643,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7644,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7645,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7646,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7647,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7648,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7649,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7650,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7651,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7652,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7653,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7654,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7655,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7656,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7657,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7658,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7659,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7660,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7661,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7662,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7663,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7664,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7665,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7666,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7667,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7668,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7669,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7670,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7671,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7672,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7673,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7674,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7675,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7676,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7677,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7678,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7679,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7680,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7681,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7682,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7683,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7684,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7685,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7686,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7687,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7688,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7689,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7690,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7691,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7692,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7693,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7694,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7695,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7696,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7697,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7698,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7699,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7700,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7701,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7702,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7703,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7704,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7705,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7706,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7707,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7708,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7709,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7710,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7711,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7712,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7713,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7714,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7715,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7716,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7717,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7718,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7719,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7720,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7721,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7722,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7723,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7724,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7725,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7726,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7727,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7728,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7729,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7730,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7731,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7732,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7733,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7734,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7735,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7736,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7737,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7738,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7739,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7740,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7741,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7742,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7743,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7744,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7745,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7746,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7747,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7748,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7749,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7750,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7751,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7752,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7753,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7754,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7755,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7756,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7757,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7758,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7759,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7760,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7761,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7762,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7763,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7764,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7765,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7766,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7767,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7768,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7769,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7770,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7771,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7772,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7773,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7774,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7775,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7776,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7777,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7778,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7779,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7780,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7781,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7782,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7783,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7784,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7785,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7786,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7787,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7788,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7789,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7790,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7791,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7792,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7793,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7794,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7795,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7796,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7797,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7798,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7799,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7800,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7801,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7802,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7803,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7804,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7805,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7806,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7807,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7808,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7809,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7810,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7811,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7812,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7813,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7814,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7815,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7816,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7817,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7818,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7819,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7820,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7821,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7822,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7823,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7824,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7825,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7826,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7827,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7828,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7829,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7830,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7831,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7832,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7833,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7834,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7835,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7836,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7837,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7838,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7839,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7840,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7841,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7842,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7843,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7844,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7845,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7846,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7847,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7848,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7849,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7850,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7851,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7852,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7853,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7854,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7855,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7856,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7857,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7858,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7859,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7860,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7861,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7862,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7863,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7864,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7865,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7866,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7867,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7868,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7869,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7870,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7871,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7872,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7873,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7874,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7875,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7876,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7877,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7878,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7879,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7880,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7881,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7882,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7883,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7884,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7885,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7886,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7887,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7888,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7889,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7890,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7891,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7892,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7893,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7894,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7895,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7896,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7897,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7898,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7899,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7900,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7901,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7902,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7903,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7904,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7905,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7906,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7907,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7908,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7909,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7910,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7911,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7912,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7913,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7914,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7915,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7916,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7917,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7918,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7919,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7920,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7921,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7922,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7923,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7924,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7925,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7926,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7927,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7928,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7929,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7930,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7931,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7932,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7933,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7934,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7935,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7936,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7937,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7938,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7939,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7940,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7941,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7942,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7943,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7944,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7945,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7946,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7947,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7948,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7949,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7950,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7951,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7952,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7953,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7954,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7955,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7956,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7957,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7958,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7959,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7960,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7961,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7962,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7963,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7964,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7965,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7966,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7967,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7968,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7969,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7970,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7971,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7972,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7973,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7974,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7975,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7976,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7977,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7978,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7979,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7980,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7981,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7982,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7983,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7984,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7985,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7986,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7987,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7988,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7989,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7990,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7991,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7992,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7993,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7994,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7995,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7996,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7997,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7998,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 7999,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8000,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8001,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8002,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8003,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8004,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8005,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8006,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8007,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8008,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8009,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8010,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8011,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8012,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8013,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8014,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8015,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8016,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8017,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8018,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8019,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8020,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8021,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8022,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8023,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8024,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8025,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8026,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8027,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8028,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8029,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8030,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8031,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8032,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8033,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8034,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8035,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8036,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8037,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8038,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8039,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8040,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8041,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8042,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8043,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8044,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8045,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8046,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8047,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8048,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8049,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8050,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8051,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8052,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8053,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8054,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8055,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8056,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8057,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8058,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8059,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8060,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8061,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8062,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8063,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8064,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8065,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8066,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8067,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8068,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8069,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8070,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8071,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8072,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8073,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8074,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8075,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8076,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8077,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8078,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8079,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8080,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8081,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8082,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8083,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8084,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8085,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8086,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8087,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8088,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8089,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8090,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8091,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8092,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8093,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8094,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8095,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8096,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8097,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8098,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8099,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8100,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8101,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8102,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8103,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8104,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8105,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8106,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8107,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8108,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8109,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8110,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8111,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8112,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8113,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8114,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8115,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8116,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8117,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8118,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8119,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8120,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8121,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8122,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8123,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8124,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8125,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8126,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8127,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8128,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8129,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8130,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8131,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8132,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8133,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8134,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8135,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8136,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8137,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8138,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8139,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8140,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8141,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8142,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8143,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8144,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8145,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8146,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8147,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8148,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8149,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8150,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8151,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8152,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8153,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8154,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8155,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8156,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8157,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8158,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8159,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8160,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8161,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8162,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8163,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8164,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8165,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8166,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8167,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8168,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8169,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8170,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8171,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8172,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8173,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8174,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8175,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8176,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8177,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8178,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8179,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8180,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8181,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8182,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8183,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8184,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8185,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8186,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8187,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8188,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8189,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8190,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8191,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8192,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8193,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8194,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8195,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8196,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8197,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8198,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8199,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8200,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8201,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8202,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8203,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8204,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8205,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8206,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8207,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8208,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8209,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8210,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8211,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8212,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8213,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8214,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8215,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8216,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8217,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8218,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8219,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8220,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8221,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8222,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8223,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8224,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8225,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8226,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8227,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8228,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8229,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8230,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8231,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8232,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8233,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8234,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8235,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8236,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8237,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8238,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8239,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8240,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8241,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8242,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8243,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8244,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8245,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8246,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8247,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8248,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8249,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8250,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8251,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8252,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8253,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8254,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8255,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8256,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8257,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8258,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8259,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8260,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8261,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8262,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8263,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8264,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8265,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8266,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8267,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8268,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8269,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8270,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8271,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8272,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8273,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8274,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8275,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8276,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8277,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8278,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8279,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8280,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8281,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8282,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8283,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8284,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8285,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8286,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8287,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8288,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8289,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8290,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8291,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8292,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8293,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8294,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8295,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8296,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8297,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8298,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8299,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8300,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8301,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8302,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8303,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8304,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8305,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8306,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8307,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8308,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8309,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8310,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8311,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8312,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8313,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8314,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8315,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8316,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8317,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8318,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8319,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8320,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8321,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8322,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8323,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8324,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8325,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8326,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8327,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8328,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8329,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8330,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8331,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8332,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8333,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8334,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8335,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8336,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8337,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8338,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8339,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8340,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8341,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8342,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8343,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8344,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8345,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8346,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8347,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8348,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8349,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8350,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8351,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8352,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8353,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8354,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8355,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8356,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8357,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8358,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8359,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8360,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8361,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8362,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8363,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8364,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8365,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8366,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8367,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8368,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8369,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8370,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8371,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8372,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8373,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8374,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8375,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8376,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8377,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8378,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8379,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8380,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8381,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8382,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8383,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8384,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8385,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8386,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8387,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8388,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8389,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8390,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8391,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8392,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8393,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8394,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8395,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8396,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8397,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8398,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8399,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8400,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8401,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8402,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8403,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8404,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8405,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8406,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8407,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8408,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8409,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8410,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8411,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8412,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8413,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8414,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8415,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8416,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8417,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8418,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8419,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8420,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8421,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8422,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8423,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8424,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8425,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8426,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8427,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8428,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8429,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8430,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8431,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8432,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8433,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8434,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8435,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8436,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8437,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8438,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8439,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8440,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8441,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8442,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8443,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8444,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8445,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8446,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8447,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8448,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8449,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8450,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8451,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8452,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8453,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8454,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8455,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8456,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8457,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8458,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8459,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8460,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8461,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8462,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8463,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8464,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8465,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8466,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8467,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8468,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8469,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8470,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8471,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8472,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8473,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8474,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8475,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8476,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8477,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8478,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8479,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8480,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8481,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8482,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8483,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8484,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8485,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8486,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8487,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8488,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8489,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8490,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8491,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8492,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8493,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8494,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8495,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8496,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8497,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8498,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8499,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8500,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8501,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8502,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8503,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8504,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8505,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8506,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8507,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8508,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8509,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8510,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8511,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8512,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8513,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8514,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8515,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8516,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8517,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8518,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8519,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8520,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8521,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8522,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8523,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8524,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8525,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8526,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8527,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8528,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8529,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8530,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8531,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8532,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8533,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8534,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8535,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8536,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8537,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8538,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8539,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8540,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8541,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8542,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8543,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8544,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8545,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8546,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8547,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8548,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8549,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8550,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8551,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8552,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8553,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8554,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8555,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8556,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8557,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8558,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8559,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8560,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8561,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8562,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8563,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8564,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8565,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8566,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8567,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8568,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8569,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8570,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8571,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8572,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8573,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8574,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8575,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8576,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8577,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8578,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8579,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8580,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8581,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8582,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8583,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8584,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8585,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8586,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8587,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8588,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8589,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8590,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8591,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8592,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8593,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8594,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8595,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8596,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8597,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8598,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8599,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8600,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8601,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8602,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8603,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8604,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8605,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8606,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8607,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8608,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8609,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8610,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8611,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8612,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8613,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8614,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8615,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8616,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8617,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8618,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8619,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8620,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8621,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8622,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8623,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8624,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8625,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8626,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8627,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8628,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8629,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8630,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8631,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8632,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8633,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8634,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8635,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8636,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8637,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8638,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8639,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8640,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8641,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8642,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8643,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8644,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8645,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8646,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8647,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8648,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8649,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8650,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8651,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8652,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8653,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8654,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8655,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8656,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8657,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8658,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8659,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8660,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8661,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8662,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8663,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8664,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8665,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8666,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8667,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8668,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8669,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8670,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8671,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8672,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8673,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8674,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8675,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8676,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8677,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8678,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8679,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8680,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8681,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8682,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8683,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8684,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8685,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8686,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8687,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8688,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8689,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8690,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8691,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8692,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8693,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8694,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8695,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8696,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8697,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8698,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8699,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8700,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8701,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8702,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8703,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8704,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8705,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8706,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8707,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8708,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8709,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8710,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8711,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8712,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8713,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8714,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8715,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8716,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8717,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8718,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8719,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8720,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8721,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8722,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8723,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8724,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8725,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8726,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8727,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8728,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8729,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8730,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8731,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8732,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8733,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8734,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8735,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8736,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8737,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8738,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8739,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8740,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8741,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8742,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8743,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8744,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8745,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8746,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8747,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8748,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8749,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8750,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8751,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8752,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8753,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8754,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8755,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8756,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8757,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8758,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8759,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8760,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8761,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8762,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8763,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8764,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8765,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8766,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8767,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8768,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8769,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8770,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8771,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8772,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8773,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8774,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8775,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8776,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8777,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8778,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8779,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8780,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8781,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8782,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8783,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8784,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8785,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8786,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8787,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8788,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8789,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8790,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8791,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8792,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8793,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8794,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8795,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8796,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8797,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8798,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8799,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8800,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8801,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8802,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8803,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8804,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8805,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8806,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8807,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8808,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8809,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8810,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8811,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8812,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8813,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8814,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8815,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8816,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8817,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8818,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8819,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8820,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8821,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8822,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8823,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8824,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8825,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8826,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8827,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8828,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8829,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8830,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8831,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8832,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8833,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8834,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8835,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8836,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8837,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8838,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8839,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8840,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8841,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8842,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8843,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8844,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8845,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8846,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8847,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8848,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8849,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8850,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8851,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8852,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8853,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8854,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8855,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8856,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8857,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8858,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8859,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8860,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8861,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8862,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8863,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8864,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8865,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8866,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8867,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8868,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8869,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8870,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8871,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8872,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8873,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8874,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8875,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8876,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8877,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8878,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8879,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8880,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8881,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8882,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8883,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8884,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8885,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8886,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8887,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8888,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8889,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8890,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8891,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8892,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8893,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8894,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8895,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8896,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8897,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8898,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8899,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8900,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8901,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8902,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8903,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8904,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8905,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8906,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8907,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8908,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8909,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8910,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8911,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8912,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8913,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8914,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8915,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8916,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8917,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8918,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8919,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8920,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8921,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8922,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8923,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8924,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8925,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8926,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8927,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8928,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8929,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8930,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8931,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8932,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8933,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8934,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8935,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8936,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8937,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8938,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8939,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8940,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8941,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8942,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8943,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8944,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8945,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8946,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8947,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8948,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8949,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8950,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8951,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8952,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8953,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8954,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8955,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8956,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8957,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8958,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8959,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8960,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8961,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8962,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8963,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8964,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8965,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8966,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8967,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8968,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8969,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8970,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8971,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8972,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8973,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8974,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8975,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8976,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8977,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8978,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8979,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8980,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8981,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8982,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8983,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8984,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8985,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8986,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8987,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8988,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8989,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8990,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8991,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8992,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8993,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8994,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8995,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8996,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8997,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8998,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 8999,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9000,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9001,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9002,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9003,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9004,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9005,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9006,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9007,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9008,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9009,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9010,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9011,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9012,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9013,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9014,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9015,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9016,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9017,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9018,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9019,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9020,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9021,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9022,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9023,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9024,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9025,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9026,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9027,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9028,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9029,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9030,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9031,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9032,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9033,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9034,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9035,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9036,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9037,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9038,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9039,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9040,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9041,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9042,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9043,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9044,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9045,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9046,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9047,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9048,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9049,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9050,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9051,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9052,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9053,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9054,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9055,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9056,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9057,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9058,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9059,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9060,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9061,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9062,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9063,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9064,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9065,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9066,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9067,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9068,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9069,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9070,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9071,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9072,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9073,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9074,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9075,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9076,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9077,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9078,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9079,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9080,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9081,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9082,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9083,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9084,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9085,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9086,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9087,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9088,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9089,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9090,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9091,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9092,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9093,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9094,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9095,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9096,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9097,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9098,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9099,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9100,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9101,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9102,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9103,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9104,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9105,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9106,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9107,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9108,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9109,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9110,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9111,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9112,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9113,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9114,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9115,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9116,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9117,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9118,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9119,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9120,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9121,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9122,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9123,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9124,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9125,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9126,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9127,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9128,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9129,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9130,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9131,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9132,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9133,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9134,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9135,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9136,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9137,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9138,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9139,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9140,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9141,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9142,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9143,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9144,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9145,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9146,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9147,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9148,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9149,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9150,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9151,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9152,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9153,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9154,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9155,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9156,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9157,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9158,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9159,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9160,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9161,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9162,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9163,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9164,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9165,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9166,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9167,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9168,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9169,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9170,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9171,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9172,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9173,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9174,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9175,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9176,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9177,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9178,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9179,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9180,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9181,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9182,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9183,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9184,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9185,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9186,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9187,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9188,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9189,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9190,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9191,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9192,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9193,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9194,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9195,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9196,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9197,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9198,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9199,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9200,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9201,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9202,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9203,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9204,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9205,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9206,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9207,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9208,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9209,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9210,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9211,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9212,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9213,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9214,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9215,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9216,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9217,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9218,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9219,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9220,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9221,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9222,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9223,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9224,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9225,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9226,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9227,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9228,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9229,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9230,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9231,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9232,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9233,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9234,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9235,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9236,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9237,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9238,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9239,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9240,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9241,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9242,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9243,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9244,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9245,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9246,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9247,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9248,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9249,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9250,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9251,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9252,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9253,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9254,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9255,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9256,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9257,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9258,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9259,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9260,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9261,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9262,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9263,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9264,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9265,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9266,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9267,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9268,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9269,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9270,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9271,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9272,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9273,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9274,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9275,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9276,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9277,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9278,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9279,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9280,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9281,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9282,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9283,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9284,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9285,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9286,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9287,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9288,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9289,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9290,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9291,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9292,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9293,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9294,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9295,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9296,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9297,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9298,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9299,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9300,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9301,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9302,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9303,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9304,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9305,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9306,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9307,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9308,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9309,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9310,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9311,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9312,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9313,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9314,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9315,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9316,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9317,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9318,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9319,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9320,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9321,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9322,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9323,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9324,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9325,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9326,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9327,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9328,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9329,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9330,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9331,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9332,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9333,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9334,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9335,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9336,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9337,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9338,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9339,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9340,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9341,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9342,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9343,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9344,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9345,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9346,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9347,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9348,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9349,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9350,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9351,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9352,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9353,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9354,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9355,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9356,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9357,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9358,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9359,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9360,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9361,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9362,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9363,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9364,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9365,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9366,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9367,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9368,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9369,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9370,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9371,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9372,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9373,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9374,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9375,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9376,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9377,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9378,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9379,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9380,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9381,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9382,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9383,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9384,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9385,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9386,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9387,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9388,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9389,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9390,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9391,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9392,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9393,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9394,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9395,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9396,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9397,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9398,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9399,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9400,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9401,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9402,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9403,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9404,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9405,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9406,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9407,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9408,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9409,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9410,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9411,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9412,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9413,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9414,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9415,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9416,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9417,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9418,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9419,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9420,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9421,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9422,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9423,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9424,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9425,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9426,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9427,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9428,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9429,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9430,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9431,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9432,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9433,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9434,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9435,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9436,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9437,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9438,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9439,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9440,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9441,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9442,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9443,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9444,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9445,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9446,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9447,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9448,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9449,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9450,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9451,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9452,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9453,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9454,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9455,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9456,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9457,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9458,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9459,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9460,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9461,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9462,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9463,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9464,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9465,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9466,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9467,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9468,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9469,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9470,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9471,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9472,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9473,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9474,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9475,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9476,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9477,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9478,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9479,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9480,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9481,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9482,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9483,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9484,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9485,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9486,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9487,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9488,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9489,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9490,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9491,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9492,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9493,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9494,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9495,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9496,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9497,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9498,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9499,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9500,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9501,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9502,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9503,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9504,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9505,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9506,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9507,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9508,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9509,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9510,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9511,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9512,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9513,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9514,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9515,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9516,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9517,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9518,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9519,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9520,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9521,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9522,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9523,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9524,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9525,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9526,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9527,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9528,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9529,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9530,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9531,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9532,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9533,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9534,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9535,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9536,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9537,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9538,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9539,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9540,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9541,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9542,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9543,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9544,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9545,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9546,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9547,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9548,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9549,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9550,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9551,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9552,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9553,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9554,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9555,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9556,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9557,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9558,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9559,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9560,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9561,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9562,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9563,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9564,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9565,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9566,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9567,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9568,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9569,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9570,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9571,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9572,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9573,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9574,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9575,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9576,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9577,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9578,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9579,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9580,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9581,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9582,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9583,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9584,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9585,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9586,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9587,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9588,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9589,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9590,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9591,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9592,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9593,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9594,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9595,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9596,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9597,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9598,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9599,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9600,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9601,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9602,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9603,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9604,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9605,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9606,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9607,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9608,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9609,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9610,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9611,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9612,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9613,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9614,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9615,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9616,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9617,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9618,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9619,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9620,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9621,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9622,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9623,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9624,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9625,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9626,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9627,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9628,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9629,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9630,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9631,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9632,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9633,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9634,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9635,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9636,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9637,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9638,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9639,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9640,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9641,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9642,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9643,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9644,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9645,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9646,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9647,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9648,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9649,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9650,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9651,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9652,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9653,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9654,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9655,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9656,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9657,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9658,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9659,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9660,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9661,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9662,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9663,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9664,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9665,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9666,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9667,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9668,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9669,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9670,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9671,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9672,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9673,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9674,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9675,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9676,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9677,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9678,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9679,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9680,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9681,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9682,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9683,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9684,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9685,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9686,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9687,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9688,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9689,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9690,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9691,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9692,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9693,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9694,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9695,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9696,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9697,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9698,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9699,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9700,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9701,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9702,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9703,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9704,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9705,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9706,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9707,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9708,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9709,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9710,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9711,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9712,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9713,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9714,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9715,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9716,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9717,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9718,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9719,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9720,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9721,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9722,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9723,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9724,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9725,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9726,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9727,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9728,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9729,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9730,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9731,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9732,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9733,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9734,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9735,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9736,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9737,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9738,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9739,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9740,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9741,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9742,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9743,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9744,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9745,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9746,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9747,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9748,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9749,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9750,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9751,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9752,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9753,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9754,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9755,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9756,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9757,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9758,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9759,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9760,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9761,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9762,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9763,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9764,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9765,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9766,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9767,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9768,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9769,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9770,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9771,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9772,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9773,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9774,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9775,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9776,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9777,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9778,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9779,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9780,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9781,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9782,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9783,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9784,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9785,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9786,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9787,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9788,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9789,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9790,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9791,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9792,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9793,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9794,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9795,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9796,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9797,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9798,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9799,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9800,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9801,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9802,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9803,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9804,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9805,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9806,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9807,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9808,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9809,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9810,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9811,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9812,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9813,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9814,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9815,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9816,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9817,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9818,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9819,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9820,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9821,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9822,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9823,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9824,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9825,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9826,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9827,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9828,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9829,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9830,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9831,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9832,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9833,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9834,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9835,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9836,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9837,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9838,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9839,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9840,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9841,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9842,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9843,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9844,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9845,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9846,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9847,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9848,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9849,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9850,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9851,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9852,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9853,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9854,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9855,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9856,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9857,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9858,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9859,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9860,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9861,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9862,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9863,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9864,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9865,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9866,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9867,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9868,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9869,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9870,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9871,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9872,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9873,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9874,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9875,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9876,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9877,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9878,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9879,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9880,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9881,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9882,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9883,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9884,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9885,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9886,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9887,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9888,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9889,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9890,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9891,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9892,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9893,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9894,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9895,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9896,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9897,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9898,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9899,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9900,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9901,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9902,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9903,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9904,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9905,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9906,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9907,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9908,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9909,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9910,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9911,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9912,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9913,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3328021628687331,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 17,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9914,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9915,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9916,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9917,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9918,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9919,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9920,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9921,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9922,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9923,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9924,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9925,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9926,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9927,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9928,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9929,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9930,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9931,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9932,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9933,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9934,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9935,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3295900536362343,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9936,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9937,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9938,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9939,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9940,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9941,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9942,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9943,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9944,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9945,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9946,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9947,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9948,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9949,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9950,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9951,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9952,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9953,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9954,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9955,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9956,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9957,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3324090144903081,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 1,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9958,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9959,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33276193604931353,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 12,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9960,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9961,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9962,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9963,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329527986839416,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9964,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33258418147689867,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 5,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9965,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9966,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3327482335456122,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 22,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9967,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9968,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321088593454361,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 24,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9969,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9970,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33211674427165777,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 10,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9971,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33289821600689834,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 23,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9972,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3322844907403588,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 15,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9973,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3320802644217105,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 14,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9974,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3309061713392811,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 26,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9975,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9976,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9977,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9978,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332932873496721,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 8,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9979,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329445629376774,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 16,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9980,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9981,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33291052861149395,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 6,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9982,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33085168348375915,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 9,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9983,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33293417082112514,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 20,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9984,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9985,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33295128041892735,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 7,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9986,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33279404860057016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9987,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9988,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.332809638267583,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 21,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9989,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.331298575890125,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 2,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9990,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3318476185917016,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 19,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9991,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9992,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329375908788027,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 18,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9993,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9994,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33253339900634704,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 11,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9995,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33127363697574913,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 25,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9996,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3321818695776968,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 0,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9997,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.33290038967015917,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 3,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9998,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3329327037149687,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 4,
    "high_priority_due_to_multiple_users": false
  },
  {
    "record_id": 9999,
    "hazard_type": "no_hazard",
    "urgency_label": "low urgency",
    "prior_hazard_at_location": false,
    "review_tag": "low_confidence",
    "duplicate_flag": true,
    "probability": 0.3323259603766181,
    "lat": null,
    "lon": null,
    "wave_altitude_proxy": null,
    "cluster_id": 13,
    "high_priority_due_to_multiple_users": false
  }
]
# Convert to DataFrame
df = pd.DataFrame(data)

# Save to CSV
df.to_csv('hazard_output.csv', index=False)
print("CSV file saved as 'hazard_output.csv'")


In [1]:
from sklearn.metrics import accuracy_score, classification_report
import numpy as np

def evaluate_pipeline(dataset_path,
                      text_model,
                      image_model,
                      audio_model,
                      meta_model,
                      device='cpu'):
    """
    Computes overall accuracy and detailed metrics for the fused model.
    """
    # reuse the same feature extraction as build_pipeline
    records = load_dataset(dataset_path)

    text_embedder = SentenceTransformer(
        'sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2'
    )
    img_transform = transforms.Compose([
        transforms.Resize((224,224)),
        transforms.ToTensor(),
        transforms.Normalize([0.485,0.456,0.406],[0.229,0.224,0.225])
    ])
    img_backbone = ImageEmbeddingModel(device=device).eval()
    ds = MultimodalDataset(records, transform=img_transform,
                           text_embedder=text_embedder)

    text_feats, image_feats, audio_feats, y_true = [], [], [], []
    for i in range(len(ds)):
        item = ds[i]
        text_feats.append(item['text_embedding'])
        with torch.no_grad():
            img_feat = img_backbone(item['image'].unsqueeze(0).to(device)).cpu().numpy().squeeze()
        image_feats.append(img_feat)
        audio_feats.append(item['audio_embedding'])
        y_true.append(item['label'])

    text_feats  = np.vstack(text_feats)
    image_feats = np.vstack(image_feats)
    audio_feats = np.vstack(audio_feats)
    y_true      = np.array(y_true)

    # probability outputs from each branch
    text_probs  = text_model.predict_proba(text_feats)
    image_probs = image_model.predict_proba(image_feats)
    audio_probs = audio_model.predict_proba(audio_feats)

    # stack highest class p
    # robabilities
    stack_X = np.vstack([
        text_probs.max(axis=1),
        image_probs.max(axis=1),
        audio_probs.max(axis=1)
    ]).T

    y_pred = meta_model.predict(stack_X)

    acc = accuracy_score(y_true, y_pred)
    print(f"\nOverall fused model accuracy: {acc:.4f}\n")
    print(classification_report(y_true, y_pred))
    return acc


ModuleNotFoundError: No module named 'sklearn'